In [1]:
import os
os.environ [ "KMP_DUPLICATE_LIB_OK" ]= "TRUE"

%load_ext autoreload
%matplotlib notebook
%autoreload 2
#!/usr/bin/env python
# -*- coding: utf-8 -*-
# @Time    : 2022/6/7 15:17
# @Author  : Wang Yujia
# @File    : mlp.ipynb
# @Description :
# @TODO:

# 0. what for
1. loss部分逻辑重写，添加`no grad`
2. 添加hooks
3. 使用pad_seq函数取代自己写的pad函数
4. 效果：可以train虽然loss不下降，不会出现NaN的问题

# 1. Preparations
## 1.1 Import

In [3]:
import pandas as pd
import numpy as np
import math
import pickle
import random
import torch.utils.data
import mydataset
from mydataset import myDataset
import torch.nn as nn
from torch.utils.data import DataLoader, SubsetRandomSampler
import torch.nn.functional as F
from torchsummary import summary
from torch.utils.tensorboard import SummaryWriter
# from tensorboardX import SummaryWriter
from visdom import Visdom
from graphviz import Digraph
import torchvision
from torchviz import make_dot
from torch.nn.utils.rnn import pad_sequence
import pygraphviz as pgv
import networkx as nx
import matplotlib.pyplot as plt
import geomloss
import time
from importlib import reload
from functools import partial
import logging
import pytorch_warmup as warmup
logging.basicConfig(filename="loss_info",filemode="w",level=logging.DEBUG)
logger = logging.getLogger(__name__)
import my_collate_fn
from torch.nn.utils import clip_grad_norm_

import scipy
from torch.nn import KLDivLoss
from torch.autograd.gradcheck import gradcheck
# from config import bcolors
from torch.cuda.amp import GradScaler,autocast
import GT_model.GT_2.SA_for_PT_funcs_delta_eq1 as GT_func
from GT_model.GT_2.SA_for_PT_funcs_delta_eq1 import *

import plotly.graph_objs as go
scaler = GradScaler(backoff_factor = 0.1)

from Config import config_MDN
# from Config import config
import loss
import plot

## 1.2 Global settings and reloading

In [4]:
reload(config_MDN)  # 必须reload！！
# reload(config)  # 必须reload！！
reload(loss)    # 必须reload！！
reload(plot)
reload(mydataset)
reload(GT_func)
reload(my_collate_fn)
from loss import cal_metric
from loss import loss_fn_v2
from loss import loss_fn_wei
from loss import loss_fn_WD
from loss import loss_fn_mse
from loss import loss_fn_CE
from loss import validate
from loss import validate_q
from plot import plot_conv_weight
from plot import plot_mu_weight
from plot import plot_pi_weight
from plot import plot_sigma_weight
from plot import plot_net
from my_collate_fn import my_collate_fn_3
from models import Conv_1_4

opt = config_MDN.DefaultConfig()

total_train_step = 0
total_test_step = 0

# Range【一般用不到】
a = 0
b = 255

device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
print(device)

cuda:0


# 2. Dataset and Dataloader
1. DataLoader中的`shuffer=True`表示在每一次epoch中都打乱所有数据的顺序，然后以batch为单位从头到尾按顺序取用数据。这样的结果就是不同epoch中的数据都是乱序的,设置随机种子的作用就是让你的每一次训练都乱的一样，

## 2.1 Dataset and spliting


- 设置随机数种子

In [ ]:
# 708 1127  469  905  732  815  471  555 1259  403  174  358  725 1087
#   510  259   74  645  484  257  178  482  965 1046 1223  323  940  130
#  1089  176  552  613  739 1067  412  568  541  375  132  208  291  241
#   962   97  612 1184  387 1058  418  365 1192  641  536  944  850 1160
#   654  586  352 1082  685 1066 1255   72 1051  296  517 1132  478  662
#  1147 1198  363 1208  766  922 1043  599 1209  109  834 1137  902 1133
#   524  348  196  453  848 1097  973 1206  796  279  601  175  506 1161
#   893  336  901  305  750  831   47  646  776  655 1143  865  397  410
#  1123    2  235  992  981 1074  701  930   73 1202  141  715  270 1268
#  1121 1204  921   48 1102 1177 1261    9  650  372  614 1112   50  278
#   413  680  415  717  874  317  842  918  606  313 1246  837   69   76
#   423  570  878  968  503  108  995  969  653  643  307  154  760 1129
#   519  138  687  792  137  720  244 1168  574  546  192 1170  222  618
#  1262  784  284  910 1022   31  696  955  420  190 1076 1236  342  900
#    37 1098  563   39  424 1049   15  271  684  814 1166  839  201  935
#   629  262   22  774 1247  823  863  704 1180  738  142   77  346  129
#   775  217  855 1057  898  754  437  979  642 1257 1056  125  490 1233
#   233  487  391   49 1126 1078  398 1122  243  633  124 1239  988  214
#   899  255  976]

In [5]:
def setup_seed(seed):
    torch.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
    np.random.seed(seed)
    random.seed(seed)
    torch.backends.cudnn.deterministic = True

setup_seed(opt.seed)

# 读取data set
dataset = myDataset(opt.train_path, opt.target_path_metric, opt.target_path_loss, opt.data_key_path, opt.NLL_metric_path)


# 在当前random seed下，设置shuffled_indices
shuffled_indices = []
DATA_len = 0
# 使用全部的data
if not opt.arr_flag:
    DATA_len = dataset.__len__()
    shuffled_indices = np.random.permutation(DATA_len)

# 使用指定的data
if opt.arr_flag:
    # shuffled_indices = np.load(opt.arr_path)
    # 用pickle读取all_data文件中的数据
    with open(opt.arr_path,'rb') as f:
        shuffled_indices = pickle.load(f)
        DATA_len = len(shuffled_indices)
    # np.random.shuffle(shuffled_indices)


train_idx = shuffled_indices[:int(opt.train_pct * DATA_len)]
if opt.SET_VAL:
    tmp = int((opt.train_pct + opt.vali_pct) * DATA_len)
    val_idx = shuffled_indices[int(opt.train_pct * DATA_len):tmp]
    test_idx = shuffled_indices[tmp:]
else :
    # Exchange. 20% for testing
    tmp = int((opt.train_pct + opt.vali_pct) * DATA_len)
    test_idx = shuffled_indices[int(opt.train_pct * DATA_len):tmp]
    val_idx = shuffled_indices[tmp:]
print(f"opt.SET_VAL = {opt.SET_VAL} and test_idx = {test_idx}")

opt.SET_VAL = False and test_idx = [ 708 1127  469  905  732  815  471  555 1259  403  174  358  725 1087
  510  259   74  645  484  257  178  482  965 1046 1223  323  940  130
 1089  176  552  613  739 1067  412  568  541  375  132  208  291  241
  962   97  612 1184  387 1058  418  365 1192  641  536  944  850 1160
  654  586  352 1082  685 1066 1255   72 1051  296  517 1132  478  662
 1147 1198  363 1208  766  922 1043  599 1209  109  834 1137  902 1133
  524  348  196  453  848 1097  973 1206  796  279  601  175  506 1161
  893  336  901  305  750  831   47  646  776  655 1143  865  397  410
 1123    2  235  992  981 1074  701  930   73 1202  141  715  270 1268
 1121 1204  921   48 1102 1177 1261    9  650  372  614 1112   50  278
  413  680  415  717  874  317  842  918  606  313 1246  837   69   76
  423  570  878  968  503  108  995  969  653  643  307  154  760 1129
  519  138  687  792  137  720  244 1168  574  546  192 1170  222  618
 1262  784  284  910 1022   31  696  955  

- 根据这个乱序排列抽取dataset

In [32]:
# 保存idx
# np.save('shuffled_indices',shuffled_indices)
# np.save('test_idx',test_idx)

## 2.2 Dataloader and collating
1. 主要是对label数据进行collate
    - 按照batch中的最大target data长度进行padding，padding with 0
2. 返回的结果多一个batch dim,比如下面的`5`
    - After collating:
        - `torch.Size([5, 3, 300]),torch.Size([5, 87, 2])`
        - `87`是最长的targets data长度

In [33]:
def test_pad_sequence():
    seq1 = torch.tensor([[ 2., 0.04761905], [3., 0.14285714], [4., 0.04761905]])
    seq2 = torch.tensor([[ 1., 0.04761905]])
    seq3 = torch.tensor([[ 3., 0.14285714], [4., 0.04761905]])
    ls = list((seq1,seq2,seq3))
    ls_length = torch.tensor([3,1,2])
    ans = pad_sequence(ls,batch_first=True)
    print(ans)
    # seq_pak = pack_padded_sequence(ans,ls_length,batch_first=True,enforce_sorted=False)
    # seq_unpacked, lens_unpacked = pad_packed_sequence(seq_pak, batch_first=True)
    # lens_unpacked

In [34]:
train_loader = DataLoader(dataset = dataset,batch_size = opt.batch_size, shuffle=False, num_workers=0, drop_last=False, sampler=SubsetRandomSampler(train_idx), collate_fn = my_collate_fn_3)

val_loader = DataLoader(dataset = dataset,batch_size = opt.batch_size, shuffle=False, num_workers=0, drop_last=False, sampler=SubsetRandomSampler(val_idx),collate_fn = my_collate_fn_3)

# 注意test_loader的batch size = 1
test_loader = DataLoader(dataset = dataset,batch_size = 1, shuffle=False, num_workers=0, drop_last=False, sampler=SubsetRandomSampler(test_idx),collate_fn = my_collate_fn_3)

# 3. The Net and Init
1. BatchNorm1d: The mean and std are calculated per-dimension over the mini-batches
2.

In [8]:
### 复现batchNorm2d在input shape为3维的情况
input = torch.tensor([[[1.,2.,3.,4.]],[[0.,0.,0.,0.]]])
# print(input.shape)
# torch.mean(input),torch.var(input,unbiased = False)
(input-torch.mean(input))/ torch.sqrt(torch.var(input,unbiased = False))

tensor([[[-0.1690,  0.5071,  1.1832,  1.8593]],

        [[-0.8452, -0.8452, -0.8452, -0.8452]]])

## 3.1 Init, Printer, Hook
- 设置网络初始权重: 不太work

In [204]:

class model_param_init(nn.Module):
    def __init__(self, model):
        super().__init__()
        assert isinstance(model, nn.Module), 'model not a class nn.Module'
        self.net = model
        self.initParam()

    def forward(self):
        for param in self.net.parameters():
            # nn.init.zeros_(param)
            # nn.init.ones_(param)
            # nn.init.normal_(param, mean=0, std=1)
            # nn.init.uniform_(param, a=0, b=1)
            # nn.init.constant_(param, val=1)   # 将所有权重初始化为1
            # nn.init.eye_(param)  # 只能将二维的tensor初始化为单位矩阵
            # nn.init.xavier_uniform_(param, gain=1)  # Glorot初始化  得到的张量是从-a——a中采用的
            # print(param)  x.unsqueeze(0)
            nn.init.xavier_normal_(param.unsqueeze(0), gain=1)   # 得到的张量是从0-std采样的
            # nn.init.kaiming_normal_(param, a=0, mode='fan_in', nonlinearity='relu') # he初始化方法
            # nn.init.kaiming_uniform_(param)

- print网络每层结构

In [ ]:
DEBUG = False
class PrintLayer(nn.Module):
    def __init__(self):
        super().__init__()

    def forward(self, x):
        if(DEBUG):
            print("This layer: ")
            print(x)      #print(x.shape)
        return x

- hook_backward_fn: 输入端的grad，输出端的grad，这里称呼的**输入与输出是站在前向传播的角度的**。如果模块有多个输入与输出的话， 其`grad_input`和`grad_output`可以是tuple类型。
- 与forward不同的是，backward传播的时候，**不仅反向传递input和output的grad，还会传递模块Parameter的grad**：
    - 比如fc模块，其`grad_input`是一个三元组的tuple，（对bias的梯度，对输入的梯度，对w的梯度）；
    - conv模块`grad_input`也是一个三元组tuple，为（对输入的梯度，对w的梯度，对bias的梯度

In [ ]:
# hook functions have to take these 3 input
def hook_forward_fn(module, input, output):
    print("It's forward: ")
    print(f"module: {module}")
    print(f"input: {input}")
    print(f"output: {output}")
    print("="*20)

def hook_backward_fn(module, grad_input, grad_output):
    print("It's backward: ")
    print(f"module: {module}")
    print(f"grad_input: {grad_input}")
    print(f"grad_output: {grad_output}")
    print("="*20)

def hook_backward_fn_pi(module, grad_input, grad_output):
    print("It's backward in pi: ")
    print(f"module: {module}")
    print(f"grad_input: {grad_input}")
    print(f"grad_output: {grad_output}")
    print("="*20)

def hook_backward_fn_sigma(module, grad_input, grad_output):
    print("It's backward in sigma: ")
    print(f"module: {module}")
    print(f"grad_input: {grad_input}")
    print(f"grad_output: {grad_output}")
    print("="*20)

def hook_backward_fn_mu(module, grad_input, grad_output):
    print("It's backward in mu: ")
    print(f"module: {module}")
    print(f"grad_input: {grad_input}")
    print(f"grad_output: {grad_output}")
    print("="*20)

## 3.2 Conv结构-1
### 3.2.1 1层conv: 1=>1
1.  Conv=>BN=>AC
2. 注意，空洞与否不是很重要

In [32]:
# 1569
class Conv_block_1(nn.Module):
    def __init__(self, ch_out=1,kernel_size=9, stride=3) -> None:
        super().__init__()

        self.kernel_size = (3,kernel_size)
        self.stride = (3,stride)
        self.ln_in = int((300-self.kernel_size[1])/self.stride[1]+1)

        self.ac_func = nn.Softplus()

        self.conv = nn.Conv2d(in_channels=1, out_channels=ch_out, kernel_size=self.kernel_size, stride=self.stride, padding=0,bias=True)
        self.BN_aff1 = nn.BatchNorm1d(num_features=1,affine=True)
        self.BN_aff2 = nn.BatchNorm1d(num_features=self.ln_in,affine=True)      # works better

    def forward(self, x):
        # Conv=>BN=>AC
        x = self.conv(x)
        # 方法一：
        # x = torch.squeeze(x,dim=2)
        # x = self.ac_func(self.BN_aff1(x))

        # 方法二：works better
        x = torch.squeeze(x)
        x = self.ac_func(self.BN_aff2(x))

        return x

class Conv_1_1(nn.Module):
    # code->generate->override methods
    def __init__(self, n_gaussians, ch_out=1, kernel_size=9, stride=3) -> None:
        super().__init__()

        self.kernel_size = (3,kernel_size)
        self.stride = (3,stride)
        self.ln_in = int((300-self.kernel_size[1])/self.stride[1]+1)

        self.BN1 = nn.BatchNorm1d(num_features=3,affine=True)

        self.layer_pi = Conv_block_1(ch_out=1,kernel_size=kernel_size,stride=stride)
        self.layer_mu = Conv_block_1(ch_out=1,kernel_size=kernel_size,stride=stride)
        self.layer_sigma = Conv_block_1(ch_out=1,kernel_size=kernel_size,stride=stride)

        self.ac_func = nn.Softplus()

        self.z_pi = nn.Sequential(
            nn.Linear(self.ln_in, n_gaussians),
            nn.Softmax(dim=1)
        )

        self.z_mu = nn.Linear(self.ln_in, n_gaussians)
        self.z_sigma = nn.Linear(self.ln_in, n_gaussians)


    def forward(self, x):

        x = self.BN1(x)
        x = torch.unsqueeze(x,dim=1)                     # torch.Size([B, 1, 3, 300])

        x_pi = torch.squeeze(self.layer_pi(x))          # 不加squeeze不行
        x_mu = torch.squeeze(self.layer_mu(x))
        x_sigma = torch.squeeze(self.layer_sigma(x))

        pi = self.z_pi(x_pi)
        mu = self.z_mu(x_mu)
        sigma = self.z_sigma(x_sigma)

        sigma = torch.exp(sigma)
        sigma = torch.clamp(sigma,1e-4)

        return pi, mu, sigma

In [33]:
mlp = Conv_1_1(opt.N_gaussians)
mlp = mlp.to(device=device)
summary(mlp, (3,300))

----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
       BatchNorm1d-1               [-1, 3, 300]               6
            Conv2d-2             [-1, 1, 1, 98]              28
       BatchNorm1d-3                   [-1, 98]             196
          Softplus-4                   [-1, 98]               0
      Conv_block_1-5                   [-1, 98]               0
            Conv2d-6             [-1, 1, 1, 98]              28
       BatchNorm1d-7                   [-1, 98]             196
          Softplus-8                   [-1, 98]               0
      Conv_block_1-9                   [-1, 98]               0
           Conv2d-10             [-1, 1, 1, 98]              28
      BatchNorm1d-11                   [-1, 98]             196
         Softplus-12                   [-1, 98]               0
     Conv_block_1-13                   [-1, 98]               0
           Linear-14                   

### 3.2.2 2层conv: 1=>1=>1
1. 比上面多了一个conv1d的提取
2. 做BN有2个思路：
    - 第一个conv结束，有91个features，BN之后接另一个Conv提取这些不同features里的信息，目的是最后得到mu等的特征
    - 第一个conv结束，有1个features，BN之后接另一个Conv提取/压缩这1个features里的信息，目的是最后得到mu等的特征

In [34]:
# 1569
class Conv_block_2(nn.Module):
    def __init__(self, ch_out=1,kernel_size=12, stride=3) -> None:
        super().__init__()

        self.kernel_size1 = (3,kernel_size)
        self.stride1 = (3,stride)
        self.ln_in = int((300-self.kernel_size1[1])/self.stride1[1]+1)

        self.ac_func = nn.Softplus()

        self.conv1 = nn.Conv2d(in_channels=1, out_channels=1, kernel_size=self.kernel_size1, stride=self.stride1, padding=0,bias=True)
        # self.BN_aff1 = nn.BatchNorm1d(num_features=1,affine=True)
        self.BN_aff1 = nn.BatchNorm1d(num_features=self.ln_in,affine=True)      # works better

        self.kernel_size2 = int(kernel_size/2)     # 可以调这个
        self.stride2 = stride
        self.ln_in2 = int((self.ln_in-self.kernel_size2)/self.stride2+1)
        self.conv2 = nn.Conv1d(in_channels=1, out_channels=ch_out, kernel_size=self.kernel_size2, stride=self.stride2, padding=0,bias=True)
        self.BN_aff2 = nn.BatchNorm1d(num_features=self.ln_in2,affine=True)      # works better

    def forward(self, x):
        # Conv=>BN=>AC
        x = self.conv1(x)
        # 方法二：works better
        x = torch.squeeze(x)
        x = self.ac_func(self.BN_aff1(x))

        x = torch.unsqueeze(x,dim=1)

        x = self.conv2(x)
        x = torch.squeeze(x)
        x = self.ac_func(self.BN_aff2(x))

        return x

class Conv_1_2(nn.Module):
    # code->generate->override methods
    def __init__(self, n_gaussians, ch_out=1, kernel_size=12, stride=3) -> None:
        super().__init__()

        self.kernel_size = (3,kernel_size)
        self.stride = (3,stride)
        # self.ln_in = int((300-self.kernel_size[1])/self.stride[1]+1)
        self.ln_in = 31

        self.BN1 = nn.BatchNorm1d(num_features=3,affine=True)

        self.layer_pi = Conv_block_2(ch_out=1,kernel_size=kernel_size,stride=stride)
        self.layer_mu = Conv_block_2(ch_out=1,kernel_size=kernel_size,stride=stride)
        self.layer_sigma = Conv_block_2(ch_out=1,kernel_size=kernel_size,stride=stride)

        self.ac_func = nn.Softplus()

        self.z_pi = nn.Sequential(
            nn.Linear(self.ln_in, n_gaussians),
            nn.Softmax(dim=1)
        )

        self.z_mu = nn.Linear(self.ln_in, n_gaussians)
        self.z_sigma = nn.Linear(self.ln_in, n_gaussians)

    def forward(self, x):

        x = self.BN1(x)
        x = torch.unsqueeze(x,dim=1)                     # torch.Size([B, 1, 3, 300])

        x_pi = torch.squeeze(self.layer_pi(x))          # 不加squeeze不行
        x_mu = torch.squeeze(self.layer_pi(x))
        x_sigma = torch.squeeze(self.layer_pi(x))

        pi = self.z_pi(x_pi)

        # mu = self.z_mu(x_mu)
        # mu = self.ac_func(self.z_mu(x_mu))
        mu = self.z_mu(x_mu)
        sigma = self.z_sigma(x_sigma)

        sigma = torch.exp(sigma)
        sigma = torch.clamp(sigma,1e-4)

        # return x_pi
        return pi, mu, sigma

In [1294]:
mlp = Conv_1_2(opt.N_gaussians)
mlp = mlp.to(device=device)
summary(mlp, (3,300))

----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
       BatchNorm1d-1               [-1, 3, 300]               6
            Conv2d-2             [-1, 1, 1, 97]              37
       BatchNorm1d-3                   [-1, 97]             194
          Softplus-4                   [-1, 97]               0
            Conv1d-5                [-1, 1, 31]               7
       BatchNorm1d-6                   [-1, 31]              62
          Softplus-7                   [-1, 31]               0
      Conv_block_2-8                   [-1, 31]               0
            Conv2d-9             [-1, 1, 1, 97]              37
      BatchNorm1d-10                   [-1, 97]             194
         Softplus-11                   [-1, 97]               0
           Conv1d-12                [-1, 1, 31]               7
      BatchNorm1d-13                   [-1, 31]              62
         Softplus-14                   

### 3.2.3 2层conv: 1=>2=>1
1. Conv2d+squeeze+conv1d

In [465]:
t,v,d,b,alpha,labda = (17470, 1299.99, 0.01, 0.75, -0.025, 3.72)
np.exp(-alpha*b)

1.0189268850520263

In [1273]:
# 573
class Conv_block_3(nn.Module):
    def __init__(self, ch_out=2,kernel_size=12, stride=3) -> None:
        super().__init__()

        self.kernel_size1 = (3,kernel_size)
        self.stride1 = (3,stride)
        self.ln_in = int((300-self.kernel_size1[1])/self.stride1[1]+1)

        self.ac_func = nn.Softplus()
        # [B, 1, 3, 300] => [B, 2, 1, ln_in]
        self.conv1 = nn.Conv2d(in_channels=1, out_channels=ch_out, kernel_size=self.kernel_size1, stride=self.stride1, padding=0,bias=True)
        self.BN_aff1 = nn.BatchNorm1d(num_features=ch_out,affine=True)


        self.kernel_size2 = int(kernel_size/2)
        self.stride2 = stride
        self.conv2 = nn.Conv1d(in_channels=ch_out, out_channels=1, kernel_size=self.kernel_size2, stride=self.stride2, padding=0,bias=True)
        self.BN_aff2 = nn.BatchNorm1d(num_features=31,affine=True)

    def forward(self, x):
        # Conv=>BN=>AC
        x = self.conv1(x)
        x = torch.squeeze(x,dim=2)  # [2, 2, 1, 97]
        x = self.ac_func(self.BN_aff1(x))

        x = torch.squeeze(x)
        # [B, 2, 97] => [B, 1, 31]
        x = self.conv2(x)
        x = torch.squeeze(x)       # [B, 1, 31] => [B, 31]
        x = self.ac_func(self.BN_aff2(x))

        return x

class Conv_1_3(nn.Module):
    # code->generate->override methods
    def __init__(self, n_gaussians, ch_out=2, kernel_size=12, stride=3) -> None:
        super().__init__()

        self.kernel_size = (3,kernel_size)
        self.stride = (3,stride)
        # self.ln_in_1 = int((300-self.kernel_size[1])/self.stride[1]+1)
        self.ln_in = 31

        self.BN1 = nn.BatchNorm1d(num_features=3,affine=True)

        self.layer_pi = Conv_block_3(ch_out=ch_out,kernel_size=kernel_size,stride=stride)
        self.layer_mu = Conv_block_3(ch_out=ch_out,kernel_size=kernel_size,stride=stride)
        self.layer_sigma = Conv_block_3(ch_out=ch_out,kernel_size=kernel_size,stride=stride)

        self.ac_func = nn.Softplus()

        self.z_pi = nn.Sequential(
            nn.Linear(self.ln_in, n_gaussians),
            nn.Softmax(dim=1)
        )

        self.z_mu = nn.Linear(self.ln_in, n_gaussians)
        self.z_sigma = nn.Linear(self.ln_in, n_gaussians)

    def forward(self, x):

        x = self.BN1(x)
        x = torch.unsqueeze(x,dim=1)                     # torch.Size([B, 1, 3, 300])

        x_pi = torch.squeeze(self.layer_pi(x))           # 不加squeeze不行
        x_mu = torch.squeeze(self.layer_pi(x))
        x_sigma = torch.squeeze(self.layer_pi(x))

        pi = self.z_pi(x_pi)

        # mu = self.z_mu(x_mu)
        mu = self.ac_func(self.z_mu(x_mu))
        sigma = self.z_sigma(x_sigma)

        sigma = torch.exp(sigma)
        sigma = torch.clamp(sigma,1e-4)

        # return x_pi
        return pi, mu, sigma

In [1256]:
mlp = Conv_1_3(opt.N_gaussians)
mlp = mlp.to(device=device)
summary(mlp, (3,300))

----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
       BatchNorm1d-1               [-1, 3, 300]               6
            Conv2d-2             [-1, 2, 1, 97]              74
       BatchNorm1d-3                [-1, 2, 97]               4
          Softplus-4                [-1, 2, 97]               0
            Conv1d-5                [-1, 1, 31]              13
       BatchNorm1d-6                   [-1, 31]              62
          Softplus-7                   [-1, 31]               0
      Conv_block_2-8                   [-1, 31]               0
            Conv2d-9             [-1, 2, 1, 97]              74
      BatchNorm1d-10                [-1, 2, 97]               4
         Softplus-11                [-1, 2, 97]               0
           Conv1d-12                [-1, 1, 31]              13
      BatchNorm1d-13                   [-1, 31]              62
         Softplus-14                   

## 3.3 Conv结构-2
1. 换了一下conv的结构

In [11]:
# 参数量747
class MLP_1_2(nn.Module):
    # code->generate->override methods
    def __init__(self, n_gaussians) -> None:
        super().__init__()
        self.BN1 = nn.BatchNorm1d(num_features=3,affine=False)
        self.BN2 = nn.BatchNorm2d(num_features=3,affine=True)
        self.BN3 = nn.BatchNorm2d(num_features=6,affine=True)
        self.drop = nn.Dropout(0.3)

        self.conv1 = nn.Conv2d(in_channels=1, out_channels=3, kernel_size=(1,6), stride=(1,3), padding=0,bias=False)
        self.ac_func = nn.Softplus()
        # self.ac_func = nn.ReLU()

        # 3, 3, 99
        self.conv2 = nn.Conv2d(in_channels=3, out_channels=6, kernel_size=(3,6), stride=6, padding=0,bias=False)
        # 6,1,33

        self.conv3 = nn.Conv2d(in_channels=6, out_channels=6, kernel_size=(1,3), stride=3, padding=0,bias=False)

        self.flatten = nn.Flatten()
        #self.linear1 = nn.Linear(48, 18)

        #无clip
        self.z_pi = nn.Sequential(
            nn.Linear(30, n_gaussians),
            nn.Softmax(dim=1)
        )

        # 有clip
        # self.z_pi = nn.Linear(30, n_gaussians)
        self.z_mu = nn.Linear(30, n_gaussians)
        self.z_sigma = nn.Linear(30, n_gaussians)

    def forward(self, x):
        x = self.BN1(x)
        # 加一个height维度

        x = torch.unsqueeze(x,dim=1)
        x = self.conv1(x)
        x = self.BN2(x)
        x = self.ac_func(self.drop(x))

        x = self.conv2(x)
        x = self.BN3(x)
        x = self.ac_func(self.drop(x))

        # x = torch.unsqueeze(x,dim=2)
        x = self.conv3(x)
        x = self.ac_func(self.drop(x))

        x = self.flatten(x)
        # x = self.linear1(x)
        # x = self.ac_func(self.drop(x))
        mu = self.z_mu(x)
        pi = self.z_pi(x)

        sigma = torch.exp(self.z_sigma(x))
        sigma = torch.clamp(sigma,1e-4)

        # return x
        return pi,mu,sigma

## 3.4 MLP结构
### 3.4.1 4层

In [12]:
# 参数量304,000+
# 4层
class MLP_1_3(nn.Module):
    # code->generate->override methods
    def __init__(self, n_gaussians) -> None:
        super().__init__()
        self.BN1 = nn.BatchNorm1d(num_features=3,affine=True)
        self.BN2 = nn.BatchNorm1d(num_features=300,affine=True)
        self.BN3 = nn.BatchNorm1d(num_features=100,affine=True)
        self.BN4 = nn.BatchNorm1d(num_features=30,affine=True)
        self.BN5 = nn.BatchNorm1d(num_features=12,affine=True)
        self.BN6 = nn.BatchNorm1d(num_features=12,affine=True)
        self.drop = nn.Dropout(0.3)

        self.linear1 = nn.Linear(900, 300)
        self.linear2 = nn.Linear(300, 100)
        self.linear3 = nn.Linear(100, 30)
        self.linear4 = nn.Linear(30, 12)

        self.ac_func = nn.Softplus()
        self.ac_func2 = nn.SELU()
        self.ac_func3 = nn.LeakyReLU()

        self.flatten = nn.Flatten()

        self.z_pi = nn.Sequential(
            nn.Linear(12, n_gaussians),  # 30个params要learn
            nn.Softmax(dim=1)
        )

        self.z_mu = nn.Linear(12, n_gaussians)
        self.z_sigma = nn.Linear(12, n_gaussians)

        # SELU Init
        # for m in self.modules():
        #     if isinstance(m, (nn.Linear)):
        #         nn.init.kaiming_normal_(m.weight, nonlinearity='linear')

    def forward(self, x):
        x = self.BN1(x)
        x = self.flatten(x)

        x = self.linear1(x)
        x = self.BN2(x)
        x = self.ac_func3(self.drop(x))

        x = self.linear2(x)
        x = self.BN3(x)
        x = self.ac_func3(self.drop(x))

        x = self.linear3(x)
        x = self.BN4(x)
        x = self.ac_func3(self.drop(x))

        x = self.linear4(x)
        x = self.BN5(x)
        x = self.ac_func3(self.drop(x))

        x = self.BN6(x)
        pi = self.z_pi(x)
        # pi = self.z_pi(torch.clamp(x,1e-3))
        mu = self.z_mu(x)
        # sigma = torch.exp(self.z_sigma(x))
        sigma = F.elu(self.z_sigma(x)) + 1
        sigma = torch.clamp(sigma,1e-4)

        # return x
        return pi, mu, sigma

### 3.4.2 2层

In [129]:
# 参数量91,000+
# 2层MLP+MDN
class MLP_1_4(nn.Module):
    # code->generate->override methods
    def __init__(self, n_gaussians) -> None:
        super().__init__()
        self.BN1 = nn.BatchNorm1d(num_features=3,affine=True)
        self.BN2 = nn.BatchNorm1d(num_features=100,affine=True)
        self.BN3 = nn.BatchNorm1d(num_features=12,affine=True)
        self.drop = nn.Dropout(0.3)

        self.linear1 = nn.Linear(900, 100)
        self.linear2 = nn.Linear(100, 12)

        self.ac_func = nn.Softplus()
        self.ac_func2 = nn.SELU()
        self.ac_func3 = nn.LeakyReLU()

        self.flatten = nn.Flatten()

        self.z_pi = nn.Sequential(
            nn.Linear(12, n_gaussians),  # 30个params要learn
            nn.Softmax(dim=1)
        )

        self.z_mu = nn.Linear(12, n_gaussians)
        self.z_sigma = nn.Linear(12, n_gaussians)


    def forward(self, x):
        # print("x.shape: ",x.shape)  # torch.Size([40, 3, 300])
        x = self.BN1(x)
        x = self.flatten(x)

        x = self.linear1(x)
        # x = self.BN2(x)
        x = self.ac_func3(self.drop(x))

        x = self.linear2(x)
        # x = self.BN3(x)
        x = self.ac_func3(self.drop(x))

        # 连续的ac？
        pi = self.z_pi(x)
        mu = self.z_mu(x)

        # sigma = torch.exp(self.z_sigma(x))
        # sigma = torch.exp(self.ac_func(self.z_sigma(x)))
        sigma = torch.exp(self.z_sigma(x))
        # sigma = F.elu(self.z_sigma(x)) + 1
        sigma = torch.clamp(sigma,1e-4)

        return pi, mu, sigma

### 3.4.4 1层+avgpool

In [238]:
# 参数量2823
# 1层MLP+MDN
class MLP_1_5(nn.Module):
    # code->generate->override methods
    def __init__(self, n_gaussians) -> None:
        super().__init__()
        self.BN1 = nn.BatchNorm1d(num_features=3,affine=True)
        self.BN2 = nn.BatchNorm1d(num_features=9,affine=True)
        self.drop = nn.Dropout(0.3)

        self.avgpool = nn.AvgPool2d(kernel_size=(1,3))  # kernel_size=(1,Channel)
        self.linear1 = nn.Linear(300, 9)

        self.ac_func = nn.Softplus()

        self.flatten = nn.Flatten()

        self.z_pi = nn.Sequential(
            nn.Linear(9, n_gaussians),  # 30个params要learn
            nn.Softmax(dim=1)
        )

        self.z_mu = nn.Linear(9, n_gaussians)
        self.z_sigma = nn.Linear(9, n_gaussians)

        # SELU Init
        # for m in self.modules():
        #     if isinstance(m, (nn.Linear)):
        #         nn.init.kaiming_normal_(m.weight, nonlinearity='linear')

        # 初始化权重
        for m in self.modules():
            if isinstance(m, nn.BatchNorm1d):
                m.weight.data.fill_(1)
                m.bias.data.zero_()
            elif isinstance(m, nn.Linear):
                # m.weight.data.normal_(0, 0.02)
                # nn.init.xavier_normal_(m.weight,gain=1)
                nn.init.orthogonal_(m.weight)
                nn.init.zeros_(m.bias)
        # nn.init.xavier_normal_(self.z_mu.weight,gain=10)

    def forward(self, x):
        x = self.BN1(x)
        # print("before transpose: ",x.shape)
        x = torch.transpose(x, 1, 2)        # [B,N,C]
        # print("before avgpool: ",x.shape)
        x = self.avgpool(x)
        # print("after avgpool: ",x.shape)
        x = self.flatten(x)

        x = self.linear1(x)
        x = self.BN2(x)
        x = self.ac_func(self.drop(x))

        pi = self.z_pi(x)
        # pi = self.z_pi(torch.clamp(x,1e-3))
        mu = self.z_mu(x)

        sigma = torch.exp(self.z_sigma(x))
        # sigma = F.elu(self.z_sigma(x)) + 1
        sigma = torch.clamp(sigma,1e-4)

        return pi, mu, sigma

In [218]:
def test_pool():
    # torch.Size([40, 3, 300])
    a = torch.tensor([[[1,2,3,4,5],[1,2,3,4,5],[1,2,3,4,5]]])
    # print(a.shape)
    a = torch.transpose(a, 1, 2)
    print(a)
    ans = F.avg_pool2d(a,(1,3))
    print(ans.shape)    # [B,N,C]
# test_pool()

### 3.4.5 1层+无avgpool

In [249]:
# 参数量8233
# 1层MLP+MDN
class MLP_1_6(nn.Module):
    # code->generate->override methods
    def __init__(self, n_gaussians) -> None:
        super().__init__()
        self.BN1 = nn.BatchNorm1d(num_features=3,affine=True)
        self.BN2 = nn.BatchNorm1d(num_features=9,affine=True)
        self.drop = nn.Dropout(0.3)

        self.linear1 = nn.Linear(900, 9)

        self.ac_func = nn.Softplus()

        self.flatten = nn.Flatten()

        self.z_pi = nn.Sequential(
            nn.Linear(9, n_gaussians),  # 30个params要learn
            nn.Softmax(dim=1)
        )

        self.z_mu = nn.Linear(9, n_gaussians)
        self.z_sigma = nn.Linear(9, n_gaussians)

        # SELU Init
        # for m in self.modules():
        #     if isinstance(m, (nn.Linear)):
        #         nn.init.kaiming_normal_(m.weight, nonlinearity='linear')

        # for m in self.modules():
        #     if isinstance(m, nn.BatchNorm1d):
        #         m.weight.data.fill_(1)
        #         m.bias.data.zero_()
        #     elif isinstance(m, nn.Linear):
        #         # m.weight.data.normal_(0, 0.02)
        #         # nn.init.xavier_normal_(m.weight,gain=1)
        #         nn.init.orthogonal_(m.weight)
        #         nn.init.zeros_(m.bias)

    def forward(self, x):
        x = self.BN1(x)
        x = self.flatten(x)

        x = self.linear1(x)
        x = self.BN2(x)
        x = self.ac_func(self.drop(x))

        pi = self.z_pi(x)
        # pi = self.z_pi(torch.clamp(x,1e-3))
        mu = self.z_mu(x)

        sigma = torch.exp(self.z_sigma(x))
        # sigma = F.elu(self.z_sigma(x)) + 1
        sigma = torch.clamp(sigma,1e-4)

        return pi, mu, sigma

## 3.5 weibull
### 3.5.1 1层conv


In [15]:
# # 1569
# class Conv_block_4(nn.Module):
#
#     def _initialize_weights(self):
#         for m in self.modules():
#             if isinstance(m, nn.Conv2d):
#                 nn.init.kaiming_normal_(m.weight, mode='fan_out', nonlinearity='relu')
#                 if m.bias is not None:
#                     nn.init.constant_(m.bias, 0)
#
#     def __init__(self, ch_out=1,kernel_size=9, stride=3, init_weight=False) -> None:
#         super().__init__()
#
#         self.kernel_size = (3,kernel_size)
#         self.stride = (3,stride)
#         self.ln_in = int((300-kernel_size)/stride+1)
#         # self.ln_in = 84
#
#         self.ac_func = nn.Softplus()
#
#         self.conv = nn.Conv2d(in_channels=1, out_channels=ch_out, kernel_size=self.kernel_size, stride=self.stride, padding=0, dilation=(1,1))
#
#         self.BN_aff2 = nn.BatchNorm1d(num_features=self.ln_in,affine=True)      # works better
#
#         if init_weight:
#             self._initialize_weights()
#
#     def forward(self, x):
#         # Conv=>BN=>AC
#         x = self.conv(x)
#         # print(x.shape)
#         # 方法一：
#         # x = torch.squeeze(x,dim=2)
#         # x = self.ac_func(self.BN_aff1(x))
#
#         # 方法二：works better
#         x = torch.flatten(x,start_dim=1)
#         x = self.ac_func(self.BN_aff2(x))
#         # x = self.ac_func(self.BN_aff1(x))
#         return x
#
# class Conv_1_4(nn.Module):
#     # code->generate->override methods
#     def __init__(self, n_gaussians, ch_out=1, kernel_size=9, stride=3) -> None:
#         super().__init__()
#
#         self.kernel_size = (3,kernel_size)
#         self.stride = (3,stride)
#         self.ln_in = int((300-self.kernel_size[1])/self.stride[1]+1)
#
#         self.BN1 = nn.BatchNorm1d(num_features=3,affine=True)
#         # self.IN1 = nn.InstanceNorm1d(num_features=3,affine=True)
#         self.layer_pi = Conv_block_4(ch_out=1,kernel_size=kernel_size,stride=stride)
#         self.layer_scale = Conv_block_4(ch_out=1,kernel_size=kernel_size,stride=stride)
#         self.layer_shape = Conv_block_4(ch_out=1,kernel_size=kernel_size,stride=stride)
#
#         self.ac_func = nn.Softplus()
#
#         self.z_pi = nn.Sequential(
#             nn.Linear(self.ln_in, n_gaussians),
#             nn.Softmax(dim=1)           # dim=0是B, dim=1才是feature
#         )
#         self.z_scale = nn.Linear(self.ln_in, n_gaussians)
#         self.z_shape = nn.Linear(self.ln_in, n_gaussians)
#
#     def forward(self, x):
#
#         x = self.BN1(x)
#         # x = self.IN1(x)
#         x = torch.unsqueeze(x,dim=1)                     # torch.Size([B, 1, 3, 300])
#
#         x_pi = self.layer_pi(x)
#         x_scale = self.layer_scale(x)
#         x_shape = self.layer_shape(x)
#
#         pi = self.z_pi(x_pi)
#         scale = torch.exp(self.z_scale(x_scale))
#         scale = torch.clamp(scale,1e-4)
#         shape = torch.exp(self.z_shape(x_shape))
#         shape = torch.clamp(shape,1e-4)
#
#         return pi,scale,shape


In [10]:
mlp = Conv_1_4(opt.N_gaussians)
mlp = mlp.to(device=device)
summary(mlp, (3,300))

----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
       BatchNorm1d-1               [-1, 3, 300]               6
            Conv2d-2             [-1, 1, 1, 98]              28
       BatchNorm1d-3                   [-1, 98]             196
          Softplus-4                   [-1, 98]               0
      Conv_block_4-5                   [-1, 98]               0
            Conv2d-6             [-1, 1, 1, 98]              28
       BatchNorm1d-7                   [-1, 98]             196
          Softplus-8                   [-1, 98]               0
      Conv_block_4-9                   [-1, 98]               0
           Conv2d-10             [-1, 1, 1, 98]              28
      BatchNorm1d-11                   [-1, 98]             196
         Softplus-12                   [-1, 98]               0
     Conv_block_4-13                   [-1, 98]               0
           Linear-14                   

- 搞成 kernel_size=[9,9,12]

In [ ]:
# # 1569
# class Conv_block_4(nn.Module):
#
#     def _initialize_weights(self):
#         for m in self.modules():
#             if isinstance(m, nn.Conv2d):
#                 nn.init.kaiming_normal_(m.weight, mode='fan_out', nonlinearity='relu')
#                 if m.bias is not None:
#                     nn.init.constant_(m.bias, 0)
#
#     def __init__(self, ch_out=1,kernel_size=9, stride=3, dilation = 1, init_weight=False) -> None:
#         super().__init__()
#
#         self.kernel_size = (3,kernel_size)
#         self.stride = (3,stride)
#         self.dilation = (1,dilation)
#         self.ln_in = int((300-kernel_size - (kernel_size-1)*(dilation-1))/stride+1)
#
#         self.ac_func = nn.Softplus()
#
#         self.conv = nn.Conv2d(in_channels=1, out_channels=ch_out, kernel_size=self.kernel_size, stride=self.stride, padding=0, dilation=self.dilation)
#         self.BN_aff2 = nn.BatchNorm1d(num_features=self.ln_in,affine=True)      # works better
#
#         if init_weight:
#             self._initialize_weights()
#
#     def forward(self, x):
#         # Conv=>BN=>AC
#         x = self.conv(x)
#         # print(x.shape)
#         # 方法一：
#         # x = torch.squeeze(x,dim=2)
#         # x = self.ac_func(self.BN_aff1(x))
#
#         # 方法二：works better
#         x = torch.flatten(x,start_dim=1)
#         x = self.ac_func(self.BN_aff2(x))
#         return x
#
# class Conv_1_4(nn.Module):
#     # code->generate->override methods
#     def __init__(self, n_gaussians, ch_out=1, kernel_size=[9,9,12],stride=[3,3,3], dilation = [1,1,2]) -> None:
#         super().__init__()
#
#         self.ln_in_1 = int((300-kernel_size[0] - (kernel_size[0]-1)*(dilation[0]-1))/stride[0]+1)
#         self.ln_in_2 = int((300-kernel_size[1] - (kernel_size[1]-1)*(dilation[1]-1))/stride[1]+1)
#         self.ln_in_3 = int((300-kernel_size[2] - (kernel_size[2]-1)*(dilation[2]-1))/stride[2]+1)
#
#         self.BN1 = nn.BatchNorm1d(num_features=3,affine=True)
#
#         self.layer_pi = Conv_block_4(ch_out=1,kernel_size=kernel_size[0],dilation = dilation[0],stride=stride[0])
#         self.layer_scale = Conv_block_4(ch_out=1,kernel_size=kernel_size[1],dilation = dilation[1],stride=stride[1])
#         self.layer_shape = Conv_block_4(ch_out=1,kernel_size=kernel_size[2],dilation = dilation[2],stride=stride[2])
#
#         self.ac_func = nn.Softplus()
#
#         self.z_pi = nn.Sequential(
#             nn.Linear(self.ln_in_1, n_gaussians),
#             nn.Softmax(dim=1)           # dim=0是B, dim=1才是feature
#         )
#
#         self.z_scale = nn.Linear(self.ln_in_2, n_gaussians)
#         self.z_shape = nn.Linear(self.ln_in_3, n_gaussians)
#
#     def forward(self, x):
#
#         x = self.BN1(x)
#         x = torch.unsqueeze(x,dim=1)                     # torch.Size([B, 1, 3, 300])
#
#         x_pi = self.layer_pi(x)
#         x_scale = self.layer_scale(x)
#         x_shape = self.layer_shape(x)
#
#         pi = self.z_pi(x_pi)
#         scale = torch.exp(self.z_scale(x_scale))
#         scale = torch.clamp(scale,1e-4)
#         shape = torch.exp(self.z_shape(x_shape))
#         shape = torch.clamp(shape,1e-4)
#
#         return pi,scale,shape


### 3.5.2 4层conv
- 上面是把(3,300)当成channel=1的图片做
- 下面是当成(3,1，300)的channel=3的图片做, 按照传统思路，缩短长度，加深channel
- BN的思路？

In [414]:
# 1569
class Conv_block_6(nn.Module):
    def __init__(self, ch_out=6,kernel_size=9, stride=3) -> None:
        super().__init__()

        self.kernel_size = (1,kernel_size)
        self.stride = (1,stride)
        self.ln_in = int((300-self.kernel_size[1])/self.stride[1]+1)

        self.ac_func = nn.Softplus()

        self.conv_1 = nn.Conv2d(in_channels=3, out_channels=6, kernel_size=self.kernel_size, stride=self.stride, padding=0,bias=True)
        self.conv_2 = nn.Conv2d(in_channels=6, out_channels=9, kernel_size=self.kernel_size, stride=self.stride, padding=0,bias=True)
        self.conv_3 = nn.Conv2d(in_channels=9, out_channels=12, kernel_size=self.kernel_size, stride=self.stride, padding=0,bias=True)
        self.conv_4 = nn.Conv2d(in_channels=12, out_channels=15, kernel_size=(1,8), stride=(1,8), padding=0,bias=True)

        self.BN_aff1 = nn.BatchNorm2d(num_features=6,affine=True)
        self.BN_aff2 = nn.BatchNorm2d(num_features=9,affine=True)
        self.BN_aff3 = nn.BatchNorm2d(num_features=12,affine=True)
        self.BN_aff4 = nn.BatchNorm2d(num_features=15,affine=True)

    def forward(self, x):
        # Conv=>BN=>AC
        x = self.conv_1(x)
        x = self.ac_func(self.BN_aff1(x))

        x = self.conv_2(x)
        x = self.ac_func(self.BN_aff2(x))

        x = self.conv_3(x)
        x = self.ac_func(self.BN_aff3(x))

        x = self.conv_4(x)
        x = self.ac_func(self.BN_aff4(x))
        x = torch.flatten(x,start_dim=1)

        return x

class Conv_1_6(nn.Module):
    # code->generate->override methods
    def __init__(self, n_gaussians, ch_out=1, kernel_size=9, stride=3) -> None:
        super().__init__()

        self.ln_in = 15

        self.BN1 = nn.BatchNorm1d(num_features=3,affine=True)

        self.layer_pi = Conv_block_6(ch_out=3,kernel_size=kernel_size,stride=stride)
        self.layer_scale = Conv_block_6(ch_out=3,kernel_size=kernel_size,stride=stride)
        self.layer_shape = Conv_block_6(ch_out=3,kernel_size=kernel_size,stride=stride)

        self.ac_func = nn.Softplus()

        self.z_pi = nn.Sequential(
            nn.Linear(self.ln_in, n_gaussians),
            nn.Softmax(dim=1)
        )
        self.z_scale = nn.Linear(self.ln_in, n_gaussians)
        self.z_shape = nn.Linear(self.ln_in, n_gaussians)

    def forward(self, x):

        x = self.BN1(x)
        x = torch.unsqueeze(x,dim=2)                     # torch.Size([B, 3, 1, 300])

        x_pi = self.layer_pi(x)
        x_scale = self.layer_scale(x)
        x_shape = self.layer_shape(x)

        pi = self.z_pi(x_pi)
        scale = torch.exp(self.z_scale(x_scale))
        scale = torch.clamp(scale,1e-4)
        shape = torch.exp(self.z_shape(x_shape))
        shape = torch.clamp(shape,1e-4)

        return pi,scale,shape

In [415]:
mlp = Conv_1_6(opt.N_gaussians)
mlp = mlp.to(device=device)
summary(mlp, (3,300))

----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
       BatchNorm1d-1               [-1, 3, 300]               6
            Conv2d-2             [-1, 6, 1, 98]             168
       BatchNorm2d-3             [-1, 6, 1, 98]              12
          Softplus-4             [-1, 6, 1, 98]               0
            Conv2d-5             [-1, 9, 1, 30]             495
       BatchNorm2d-6             [-1, 9, 1, 30]              18
          Softplus-7             [-1, 9, 1, 30]               0
            Conv2d-8             [-1, 12, 1, 8]             984
       BatchNorm2d-9             [-1, 12, 1, 8]              24
         Softplus-10             [-1, 12, 1, 8]               0
           Conv2d-11             [-1, 15, 1, 1]           1,455
      BatchNorm2d-12             [-1, 15, 1, 1]              30
         Softplus-13             [-1, 15, 1, 1]               0
     Conv_block_6-14                   

- 空洞卷积

In [ ]:
# 1569
class Conv_block_8(nn.Module):
    def __init__(self, ch_out=6,kernel_size=9, stride=3) -> None:
        super().__init__()

        self.kernel_size = (1,kernel_size)
        self.stride = (1,stride)
        self.ln_in = int((300-self.kernel_size[1])/self.stride[1]+1)

        self.ac_func = nn.Softplus()

        self.conv_1 = nn.Conv2d(in_channels=3, out_channels=6, kernel_size=self.kernel_size, stride=self.stride, padding=0,bias=True)
        self.conv_2 = nn.Conv2d(in_channels=6, out_channels=9, kernel_size=self.kernel_size, stride=self.stride, padding=0,bias=True)
        self.conv_3 = nn.Conv2d(in_channels=9, out_channels=12, kernel_size=self.kernel_size, stride=self.stride, padding=0,bias=True)
        self.conv_4 = nn.Conv2d(in_channels=12, out_channels=15, kernel_size=(1,8), stride=(1,8), padding=0,bias=True)

        self.BN_aff1 = nn.BatchNorm2d(num_features=6,affine=True)
        self.BN_aff2 = nn.BatchNorm2d(num_features=9,affine=True)
        self.BN_aff3 = nn.BatchNorm2d(num_features=12,affine=True)
        self.BN_aff4 = nn.BatchNorm2d(num_features=15,affine=True)

    def forward(self, x):
        # Conv=>BN=>AC
        x = self.conv_1(x)
        x = self.ac_func(self.BN_aff1(x))

        x = self.conv_2(x)
        x = self.ac_func(self.BN_aff2(x))

        x = self.conv_3(x)
        x = self.ac_func(self.BN_aff3(x))

        x = self.conv_4(x)
        x = self.ac_func(self.BN_aff4(x))
        x = torch.flatten(x,start_dim=1)

        return x

class Conv_1_8(nn.Module):
    # code->generate->override methods
    def __init__(self, n_gaussians, ch_out=1, kernel_size=9, stride=3) -> None:
        super().__init__()

        self.ln_in = 15

        self.BN1 = nn.BatchNorm1d(num_features=3,affine=True)

        self.layer_pi = Conv_block_8(ch_out=3,kernel_size=kernel_size,stride=stride)
        self.layer_scale = Conv_block_8(ch_out=3,kernel_size=kernel_size,stride=stride)
        self.layer_shape = Conv_block_8(ch_out=3,kernel_size=kernel_size,stride=stride)

        self.ac_func = nn.Softplus()

        self.z_pi = nn.Sequential(
            nn.Linear(self.ln_in, n_gaussians),
            nn.Softmax(dim=1)
        )
        self.z_scale = nn.Linear(self.ln_in, n_gaussians)
        self.z_shape = nn.Linear(self.ln_in, n_gaussians)

    def forward(self, x):

        x = self.BN1(x)
        x = torch.unsqueeze(x,dim=2)                     # torch.Size([B, 3, 1, 300])

        x_pi = self.layer_pi(x)
        x_scale = self.layer_scale(x)
        x_shape = self.layer_shape(x)

        pi = self.z_pi(x_pi)
        scale = torch.exp(self.z_scale(x_scale))
        scale = torch.clamp(scale,1e-4)
        shape = torch.exp(self.z_shape(x_shape))
        shape = torch.clamp(shape,1e-4)

        return pi,scale,shape

### 3.5.3 2层conv

In [190]:
# 1569
class Conv_block_5_1(nn.Module):
    def __init__(self, ch_out=3,kernel_size=12, stride=3) -> None:
        super().__init__()

        self.kernel_size = (3,kernel_size)
        self.stride = (3,stride)
        self.ln_in = int((300-self.kernel_size[1])/self.stride[1]+1)

        self.ac_func = nn.Softplus()

        self.conv = nn.Conv2d(in_channels=1, out_channels=ch_out, kernel_size=self.kernel_size, stride=self.stride, padding=0,bias=True)
        self.BN_aff1 = nn.BatchNorm1d(num_features=ch_out,affine=True)
        self.BN_aff2 = nn.BatchNorm1d(num_features=self.ln_in,affine=True)      # works better

    def forward(self, x):
        # Conv=>BN=>AC
        x = self.conv(x)
        # 方法一：
        x = torch.squeeze(x,dim=2)
        x = self.ac_func(self.BN_aff1(x))
        return x


class Conv_block_5_2(nn.Module):
    def __init__(self, ch_in = 3, ch_out=6,kernel_size=9, stride=3) -> None:
        super().__init__()

        self.kernel_size = (3,kernel_size)
        self.stride = (3,stride)
        self.ln_in = int((97-self.kernel_size[1])/self.stride[1]+1)

        self.ac_func = nn.Softplus()

        self.conv = nn.Conv2d(in_channels=ch_in, out_channels=ch_out, kernel_size=self.kernel_size, stride=self.stride, padding=0,bias=True)
        self.BN_aff1 = nn.BatchNorm1d(num_features=ch_out,affine=True)
        self.BN_aff2 = nn.BatchNorm1d(num_features=self.ln_in,affine=True)      # works better

    def forward(self, x):
        # Conv=>BN=>AC
        x = self.conv(x)
        # 方法一：
        x = torch.squeeze(x,dim=2)
        x = self.ac_func(self.BN_aff1(x))
        return x


class Conv_1_5(nn.Module):
    # code->generate->override methods
    def __init__(self, n_gaussians, ch_out=1, kernel_size=12, stride=3) -> None:
        super().__init__()

        self.kernel_size = (3,kernel_size)
        self.stride = (3,stride)
        self.ln_in = int((300-self.kernel_size[1])/self.stride[1]+1)

        self.BN1 = nn.BatchNorm1d(num_features=3,affine=True)

        self.layer_pi = Conv_block_5_1(ch_out=3,kernel_size=kernel_size,stride=stride)
        self.layer_scale = Conv_block_5_1(ch_out=3,kernel_size=kernel_size,stride=stride)
        self.layer_shape = Conv_block_5_1(ch_out=3,kernel_size=kernel_size,stride=stride)

        self.ac_func = nn.Softplus()

        self.z_pi = nn.Sequential(
            nn.Linear(self.ln_in, n_gaussians),
            nn.Softmax(dim=1)
        )
        self.z_scale = nn.Linear(self.ln_in, n_gaussians)
        self.z_shape = nn.Linear(self.ln_in, n_gaussians)

    def forward(self, x):

        x = self.BN1(x)
        x = torch.unsqueeze(x,dim=1)                     # torch.Size([B, 1, 3, 300])

        x_pi = torch.squeeze(self.layer_pi(x))          # 不加squeeze不行
        x_scale = torch.squeeze(self.layer_scale(x))
        x_shape = torch.squeeze(self.layer_shape(x))

        pi = self.z_pi(x_pi)
        scale = torch.exp(self.z_scale(x_scale))
        scale = torch.clamp(scale,1e-4)
        shape = torch.exp(self.z_shape(x_shape))
        shape = torch.clamp(shape,1e-4)

        return x_pi,x_scale,x_shape

In [191]:
mlp = Conv_1_5(opt.N_gaussians)
mlp = mlp.to(device=device)
summary(mlp, (3,300))

----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
       BatchNorm1d-1               [-1, 3, 300]               6
            Conv2d-2             [-1, 3, 1, 97]             111
       BatchNorm1d-3                [-1, 3, 97]               6
          Softplus-4                [-1, 3, 97]               0
    Conv_block_5_1-5                [-1, 3, 97]               0
            Conv2d-6             [-1, 3, 1, 97]             111
       BatchNorm1d-7                [-1, 3, 97]               6
          Softplus-8                [-1, 3, 97]               0
    Conv_block_5_1-9                [-1, 3, 97]               0
           Conv2d-10             [-1, 3, 1, 97]             111
      BatchNorm1d-11                [-1, 3, 97]               6
         Softplus-12                [-1, 3, 97]               0
   Conv_block_5_1-13                [-1, 3, 97]               0
Total params: 357
Trainable params: 357

### 3.5.3 MLP

In [322]:
# 参数量91,000+
# 2层MLP+MDN
class MLP_1_7(nn.Module):
    # code->generate->override methods
    def __init__(self, n_gaussians) -> None:
        super().__init__()
        self.BN1 = nn.BatchNorm1d(num_features=3,affine=True)
        self.BN2 = nn.BatchNorm1d(num_features=100,affine=True)
        self.BN3 = nn.BatchNorm1d(num_features=12,affine=True)
        self.drop = nn.Dropout(0.3)

        self.linear1 = nn.Linear(900, 100)
        self.linear2 = nn.Linear(100, 12)

        self.ac_func = nn.Softplus()
        self.ac_func2 = nn.SELU()
        self.ac_func3 = nn.LeakyReLU()

        self.flatten = nn.Flatten()

        self.z_pi = nn.Sequential(
            nn.Linear(12, n_gaussians),  # 30个params要learn
            nn.Softmax(dim=1)
        )

        self.z_scale = nn.Linear(12, n_gaussians)
        self.z_shape = nn.Linear(12, n_gaussians)


    def forward(self, x):
        # print("x.shape: ",x.shape)  # torch.Size([40, 3, 300])
        x = self.BN1(x)
        x = self.flatten(x)

        x = self.linear1(x)
        x = self.BN2(x)
        x = self.ac_func3(self.drop(x))

        x = self.linear2(x)
        x = self.BN3(x)
        x = self.ac_func3(self.drop(x))

        pi = self.z_pi(x)

        scale = torch.exp(self.z_scale(x))
        scale = torch.clamp(scale,1e-4)
        shape = torch.exp(self.z_shape(x))
        shape = torch.clamp(shape,1e-4)

        return pi, scale, shape

### 3.5.4 depth-wise separable conv
1. 没差
2. 先depth-wise再用1×1
3. 添加了residual结构，还不如不用。。

In [854]:
# 1569
class Conv_block_7(nn.Module):
    def __init__(self, ch_out=1,kernel_size=9, stride=3) -> None:
        super().__init__()

        self.kernel_size = (3,kernel_size)
        self.stride = (3,stride)
        # self.ln_in = int((300-kernel_size)/stride+1)
        self.ln_in = 84

        self.ac_func = nn.Softplus()

        self.conv1 = nn.LazyConv1d(out_channels=2*3,kernel_size=9,stride=3,groups=3)
        self.conv2 = nn.LazyConv1d(out_channels=4*3,kernel_size=6,stride=3,groups=2*3)
        self.conv3 = nn.LazyConv1d(out_channels=8*3,kernel_size=4,stride=4,groups=4*3)
        self.conv4 = nn.LazyConv1d(out_channels=3,kernel_size=1,stride=1)   # 1×1

        self.BN_aff1 = nn.BatchNorm1d(num_features=2*3,affine=True)
        self.BN_aff2 = nn.BatchNorm1d(num_features=4*3,affine=True)
        self.BN_aff3 = nn.BatchNorm1d(num_features=8*3,affine=True)
        self.BN_aff4 = nn.BatchNorm1d(num_features=3,affine=True)

    def forward(self, input):
        # Conv=>BN=>AC
        x = self.conv1(input)
        x = self.ac_func(self.BN_aff1(x))

        x = self.conv2(x)
        x = self.ac_func(self.BN_aff2(x))

        x = self.conv3(x)
        x = self.ac_func(self.BN_aff3(x))

        x = self.conv4(x)
        x = self.ac_func(self.BN_aff4(x))

        x = torch.flatten(x,start_dim=1)

        return x

class Conv_1_7(nn.Module):
    # code->generate->override methods
    def __init__(self, n_gaussians, ch_out=1, kernel_size=9, stride=3) -> None:
        super().__init__()

        self.kernel_size = (3,kernel_size)
        self.stride = (3,stride)
        # self.ln_in = int((300-self.kernel_size[1])/self.stride[1]+1)
        self.ln_in = 21

        self.BN1 = nn.BatchNorm1d(num_features=3,affine=True)
        # out_channels == K * in_channels
        # 有in_channels个group,每一个group有K个卷积核，能产生K张特征图，所以最后的输出是Cin*K.

        self.layer_pi = Conv_block_7(ch_out=1,kernel_size=kernel_size,stride=stride)
        self.layer_scale = Conv_block_7(ch_out=1,kernel_size=kernel_size,stride=stride)
        self.layer_shape = Conv_block_7(ch_out=1,kernel_size=kernel_size,stride=stride)

        self.ac_func = nn.Softplus()

        self.z_pi = nn.Sequential(
            nn.Linear(self.ln_in, n_gaussians),
            nn.Softmax(dim=1)           # dim=0是B, dim=1才是feature
        )
        self.z_scale = nn.Linear(self.ln_in, n_gaussians)
        self.z_shape = nn.Linear(self.ln_in, n_gaussians)

    def forward(self, x):

        x = self.BN1(x)
        # x = torch.unsqueeze(x,dim=1)                     # torch.Size([B, 1, 3, 300])

        x_pi = self.layer_pi(x)
        x_scale = self.layer_scale(x)
        x_shape = self.layer_shape(x)

        pi = self.z_pi(x_pi)
        scale = torch.exp(self.z_scale(x_scale))
        scale = torch.clamp(scale,1e-4)
        shape = torch.exp(self.z_shape(x_shape))
        shape = torch.clamp(shape,1e-4)

        return pi,scale,shape
        # return pi

In [855]:
mlp = Conv_1_7(opt.N_gaussians,kernel_size=9,stride=3)
mlp = mlp.to(device=device)
summary(mlp, (3,300))

----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
       BatchNorm1d-1               [-1, 3, 300]               6
            Conv1d-2                [-1, 6, 98]              60
       BatchNorm1d-3                [-1, 6, 98]              12
          Softplus-4                [-1, 6, 98]               0
            Conv1d-5               [-1, 12, 31]              84
       BatchNorm1d-6               [-1, 12, 31]              24
          Softplus-7               [-1, 12, 31]               0
            Conv1d-8                [-1, 24, 7]             120
       BatchNorm1d-9                [-1, 24, 7]              48
         Softplus-10                [-1, 24, 7]               0
           Conv1d-11                 [-1, 3, 7]              75
      BatchNorm1d-12                 [-1, 3, 7]               6
         Softplus-13                 [-1, 3, 7]               0
           Conv1d-14                 [-

D:\Anaconda\Lib\site-packages\torch\nn\modules\lazy.py:180: UserWarning: Lazy modules are a new feature under heavy development so changes to the API or functionality can happen at any moment.
  warnings.warn('Lazy modules are a new feature under heavy development '


### 3.5.5 Conv + 不同的kernel设计
1. weibull的shape关注的是？scale关注的是？后者比前者感受野要小？

In [28]:
# 1569
class Conv_block_9(nn.Module):

    def _initialize_weights(self):
        for m in self.modules():
            if isinstance(m, nn.Conv2d):
                nn.init.kaiming_normal_(m.weight, mode='fan_out', nonlinearity='relu')
                if m.bias is not None:
                    nn.init.constant_(m.bias, 0)

    def __init__(self, ch_out=1,kernel_size=9, stride=3, dilation=1,init_weight=False) -> None:
        super().__init__()

        self.kernel_size = (3,kernel_size)
        self.stride = (3,stride)
        self.ln_in = int((300-kernel_size-(kernel_size-1)*(dilation-1))/stride+1)
        # self.ln_in = 84

        self.ac_func = nn.Softplus()

        self.conv = nn.Conv2d(in_channels=1, out_channels=ch_out, kernel_size=self.kernel_size, stride=self.stride, padding=0, dilation=(1,dilation))
        self.BN_aff1 = nn.BatchNorm1d(num_features=1,affine=True)
        self.BN_aff2 = nn.BatchNorm1d(num_features=self.ln_in,affine=True)      # works better

        if init_weight:
            self._initialize_weights()

    def forward(self, x):
        # Conv=>BN=>AC
        x = self.conv(x)
        # print(x.shape)
        # 方法一：
        # x = torch.squeeze(x,dim=2)
        # x = self.ac_func(self.BN_aff1(x))

        # 方法二：works better
        x = torch.flatten(x,start_dim=1)
        x = self.ac_func(self.BN_aff2(x))
        return x

class Conv_1_9(nn.Module):
    # code->generate->override methods
    def __init__(self, n_gaussians, ch_out=1, kernel_size=9, stride=3) -> None:
        super().__init__()

        self.kernel_size = (3,kernel_size)
        self.stride = (3,stride)
        self.ln_in = int((300-self.kernel_size[1])/self.stride[1]+1)
        self.ln_scale = int((300-self.kernel_size[1])/self.stride[1]+1)
        self.ln_shape = 36

        self.BN1 = nn.BatchNorm1d(num_features=3,affine=True)

        self.layer_pi = Conv_block_9(ch_out=1,kernel_size=kernel_size,stride=stride)
        self.layer_scale = Conv_block_9(ch_out=1,kernel_size=kernel_size,stride=stride)
        self.layer_shape = Conv_block_9(ch_out=1,kernel_size=30,stride=6,dilation=3)

        self.ac_func = nn.Softplus()

        self.z_pi = nn.Sequential(
            nn.Linear(self.ln_in, n_gaussians),
            nn.Softmax(dim=1)           # dim=0是B, dim=1才是feature
        )
        self.z_scale = nn.Linear(self.ln_scale, n_gaussians)
        self.z_shape = nn.Linear(self.ln_shape, n_gaussians)

    def forward(self, x):

        x = self.BN1(x)
        x = torch.unsqueeze(x,dim=1)                     # torch.Size([B, 1, 3, 300])

        x_pi = self.layer_pi(x)
        x_scale = self.layer_scale(x)
        x_shape = self.layer_shape(x)

        pi = self.z_pi(x_pi)
        scale = torch.exp(self.z_scale(x_scale))
        scale = torch.clamp(scale,1e-4)
        shape = torch.exp(self.z_shape(x_shape))
        shape = torch.clamp(shape,1e-4)

        return pi,scale,shape

In [29]:
mlp = Conv_1_9(opt.N_gaussians)
mlp = mlp.to(device=device)
summary(mlp, (3,300))

----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
       BatchNorm1d-1               [-1, 3, 300]               6
            Conv2d-2             [-1, 1, 1, 98]              28
       BatchNorm1d-3                   [-1, 98]             196
          Softplus-4                   [-1, 98]               0
      Conv_block_9-5                   [-1, 98]               0
            Conv2d-6             [-1, 1, 1, 98]              28
       BatchNorm1d-7                   [-1, 98]             196
          Softplus-8                   [-1, 98]               0
      Conv_block_9-9                   [-1, 98]               0
           Conv2d-10             [-1, 1, 1, 36]              91
      BatchNorm1d-11                   [-1, 36]              72
         Softplus-12                   [-1, 36]               0
     Conv_block_9-13                   [-1, 36]               0
           Linear-14                   

## 3.6 分开设计
1. 分别用2个通路，对两个GT模型进行learning

In [313]:
class Conv_block_(nn.Module):

    def _initialize_weights(self):
        for m in self.modules():
            if isinstance(m, nn.Conv2d):
                nn.init.kaiming_normal_(m.weight, mode='fan_out', nonlinearity='relu')
                if m.bias is not None:
                    nn.init.constant_(m.bias, 0)

    def __init__(self, ch_out=1,kernel_size=9, stride=3, dilation=1,init_weight=False) -> None:
        super().__init__()

        self.kernel_size = (2,kernel_size)
        self.stride = (2,stride)
        self.ln_in = int((300-kernel_size-(kernel_size-1)*(dilation-1))/stride+1)

        self.ac_func = nn.Softplus()

        self.conv = nn.Conv2d(in_channels=1, out_channels=ch_out, kernel_size=self.kernel_size, stride=self.stride, padding=0, dilation=(1,dilation))
        self.BN_aff = nn.BatchNorm1d(num_features=self.ln_in,affine=True)      # works better

        if init_weight:
            self._initialize_weights()

    def forward(self, x):
        # Conv=>BN=>AC
        x = self.conv(x)
        x = torch.flatten(x,start_dim=1)
        x = self.ac_func(self.BN_aff(x))
        return x

class GT_block_2_1(nn.Module):

    def _initialize_weights(self):
        for m in self.modules():
            if isinstance(m, nn.Conv2d):
                nn.init.kaiming_normal_(m.weight, mode='fan_out', nonlinearity='relu')
                if m.bias is not None:
                    nn.init.constant_(m.bias, 0)

    def __init__(self, ch_out=1,kernel_size=[9,9,30], stride=[3,3,6], dilation = 3,init_weight=False) -> None:
        super().__init__()

        self.ln_in = int((300-kernel_size[0])/stride[0]+1)
        self.ln_scale = int((300-kernel_size[1])/stride[1]+1)
        self.ln_shape = int((300-kernel_size[2] - (kernel_size[2]-1)*(dilation-1))/stride[2]+1)

        self.ac_func = nn.Softplus()

        self.layer_pi = Conv_block_(ch_out=1,kernel_size=kernel_size[0],stride=stride[0])
        self.layer_scale = Conv_block_(ch_out=1,kernel_size=kernel_size[1],stride=stride[1])
        self.layer_shape = Conv_block_(ch_out=1,kernel_size=kernel_size[2],stride=stride[2],dilation=dilation)

        self.z_pi = nn.Sequential(
            nn.Linear(self.ln_in, 1),
            nn.Sigmoid()           # dim=0是B, dim=1才是feature
        )
        self.z_scale = nn.Linear(self.ln_scale, 1)
        self.z_shape = nn.Linear(self.ln_shape, 1)

        if init_weight:
            self._initialize_weights()

    def forward(self, x):
        x_pi = self.layer_pi(x)
        x_scale = self.layer_scale(x)
        x_shape = self.layer_shape(x)

        pi = self.z_pi(x_pi)
        scale = torch.exp(self.z_scale(x_scale))
        scale = torch.clamp(scale,1e-4)
        shape = torch.exp(self.z_shape(x_shape))
        shape = torch.clamp(shape,1e-4)
        return pi,scale,shape

class Conv_2_1(nn.Module):
    def __init__(self,n_GT,kernel_size=[9,9,30], stride=[3,3,6],dilation = 3,init_weight = False):
        super().__init__()

        self.BN1 = nn.BatchNorm1d(num_features=2,affine=True)
        self.BN2 = nn.BatchNorm1d(num_features=2,affine=True)

        self.layer_GT_1 = GT_block_2_1(ch_out=1,kernel_size=kernel_size,stride=stride,dilation=dilation,init_weight = init_weight)
        self.layer_GT_2 = GT_block_2_1(ch_out=1,kernel_size=kernel_size,stride=stride,dilation=dilation,init_weight = init_weight)

        self.layer_pi_all = nn.Softmax(dim=1)

    def forward(self, x):

        x1 = self.BN1(x[: ,0:2, :])
        x1 = torch.unsqueeze(x1,dim=1)                     # torch.Size([B, 1, 3, 300])
        x2 = self.BN2(x[: ,2:4, :])
        x2 = torch.unsqueeze(x2,dim=1)                     # torch.Size([B, 1, 3, 300])

        pi_1,scale_1,shape_1 = self.layer_GT_1(x1)
        pi_2,scale_2,shape_2 = self.layer_GT_2(x2)

        pi = torch.cat([pi_1,pi_2],dim=1)
        scale = torch.cat([scale_1,scale_2],dim=1)
        shape = torch.cat([shape_1,shape_2],dim=1)
        pi = self.layer_pi_all(pi)

        return pi,scale,shape

In [114]:
mlp = Conv_2_1(opt.N_gaussians)
mlp = mlp.to(device=device)
summary(mlp, (4,300),batch_size=10)

----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
       BatchNorm1d-1               [10, 2, 300]               4
       BatchNorm1d-2               [10, 2, 300]               4
            Conv2d-3             [10, 1, 1, 98]              19
       BatchNorm1d-4                   [10, 98]             196
          Softplus-5                   [10, 98]               0
       Conv_block_-6                   [10, 98]               0
            Conv2d-7             [10, 1, 1, 98]              19
       BatchNorm1d-8                   [10, 98]             196
          Softplus-9                   [10, 98]               0
      Conv_block_-10                   [10, 98]               0
           Conv2d-11             [10, 1, 1, 36]              61
      BatchNorm1d-12                   [10, 36]              72
         Softplus-13                   [10, 36]               0
      Conv_block_-14                   

- 两个MDN分别train两个dataset

# 4. The Loss
## 4.0 The metric
1. 以NLL作为metric
2. 理论模型的metric已经提前算好，读进来.
3. 注意这里的metric比较的是target还是target_5:
    - 建议使用target data而不是target_5，因为后者是为了方便NN的learning，前者才是真正的比较NLL
    - 使用前者也要用cdf进行比较吧。。比如GT的4实际上是我们这里的[3.5,4.5]？是高斯分布在[a-0.5,a+0.5]上的cdf作为a的“单点分布”

In [48]:
# from loss import cal_metric

## 4.1 NLL loss
### 4.1.1 original version

In [42]:
# from loss import loss_fn_v2

### 4.1.2 version 3 [LogSumExp]
1. $ exponent_i = \log_{}{\alpha_i } -1/2*\log_{}{2\pi } -\log_{}{\sigma_i }- \frac{(x-\mu_i )^2}{2\sigma_i^2} $
2. $ NLL =-\sum_{j}^{N_S}LogSumExp= -\sum_{j}^{N_S} \log\sum_{i}^{N_G} \exp \{exponent_i\}$
3. 不稳定！lr不要设超过1e-2；而且loss会变成负值。。最开始x_max是负值，后面会变成正值 which means prob值开始>1了

In [ ]:
from loss import log_sum_exp
from loss import loss_fn_v3

## 4.2 cdf loss
1. 注意把targets data的路径改一下

In [21]:
# cdf loss
from loss import loss_fn_cdf

## 4.3 交叉熵/ KL
1. 自己写的，没有用torch的函数

In [ ]:
from loss import loss_fn_CE

In [ ]:
def loss_test():
    loss_2 = torch.tensor([1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.])
    loss_3 = loss_2[torch.nonzero(loss_2)].view(-1,1)         # 去掉所有的log(0)
    print("loss_3:",loss_3.shape)

    MIN_LOSS = torch.min(loss_2) if torch.min(loss_2)>0 else 1e-20

    print("MIN_LOSS：",MIN_LOSS)
    # 用MIN_loss替代loss_2为0的部分
    loss_2[loss_2==0] = MIN_LOSS


    loss_padded = [MIN_LOSS]* (loss_2.shape[0]-loss_3.shape[0])
    loss_padded_ts = torch.tensor(loss_padded) # ,device=device
    loss_3 = torch.cat((loss_3[:,0],loss_padded_ts))
    loss_3.shape, torch.log(loss_3)
    print("data: ",loss_3.data)
    print("data: ",type(loss_3))
# loss_test()

## 4.4 W-distance
1. 拿到target data的两列，按照第一列去predict
2. Ref: https://www.kernel-operations.io/geomloss/api/pytorch-api.html

# 5 Plot
1. draw:
    - loss: training data的loss和test data的loss趋势
    - MLP的网络结构（.png）
    - target distrb.和pred. distrb.
    - 所有target data的分布图


In [14]:
env_str = "001"
viz = Visdom(env=env_str)

## 5.1 draw 所有的target data
1. 实际上在`i < 50`里决定画前50 or what target data

In [11]:
def draw_all_target_data():
    # target data
    # target_path = r"../data/targets"
    target_path = r"../data/targets_5"
    # target_path里有全部的target data地址
    target_all_path = os.listdir(target_path)
    len_target = len(target_all_path)
    print(f"一共有 *{len_target}* 组 target data")

    # Init
    # viz_env_str = "target_bar"
    # viz_env_str = "target_line"
    # viz_env_str = "target_hist"
    viz_env_str = "target_scatter"
    viz = Visdom(env = viz_env_str)

    for i in range(len_target):
        target_path_i_path = os.path.join(target_path,target_all_path[i])
        target_df = pd.read_csv(target_path_i_path,encoding="utf-8")

        # Init
        win_str = str(target_all_path[i])
        title_str = "Target Distrb. of "+win_str

        if(i < 50):
            # Hist plot which is not that great
            if viz_env_str == "target_hist" :
                viz.histogram(X = np.array(target_df.N), env=viz_env_str, win=win_str,
                            opts= dict(title=title_str,numbins = 50))

            # Line plot
            if viz_env_str == "target_line" :
                target_df.drop_duplicates(inplace=True)
                viz.line(X = np.array(target_df.N),Y= np.array(target_df.P), env=viz_env_str, win=win_str,opts= dict(title=title_str,markers = True,markersize = 7,markersymbol = "cross-thin-open"))

            # Bar plot. 这个看起来是最准确的一个
            if viz_env_str == "target_bar" :
                target_df.drop_duplicates(inplace=True)
                arr_str = [str(i) for i in np.array(target_df.N)]
                viz.bar(X=np.array(target_df.P), env=viz_env_str, win=win_str,
                        opts=dict(title=title_str,rownames=arr_str,stacked = False))

            # Scatter plot
            if viz_env_str == "target_scatter" :
                target_df.drop_duplicates(inplace=True)
                viz.scatter(X=np.array(target_df),env=viz_env_str, win=win_str,opts=dict(title=title_str,markersize = 3))
    print("Done")

# draw_all_target_data()

- 画target data的cdf

In [9]:
def draw_all_target_data_cdf():
    # target data
    # target_path = r"../data/targets"
    target_path = r"../data/targets_5_cdf"
    # target_path里有全部的target data地址
    target_all_path = os.listdir(target_path)
    len_target = len(target_all_path)
    print(f"一共有 *{len_target}* 组 target data")

    # Init，只需要改这个str就ok
    # viz_env_str = "target_barCDF"
    # viz_env_str = "target_lineCDF"
    # viz_env_str = "target_histCDF"
    viz_env_str = "target_scatterCDF"
    viz = Visdom(env = viz_env_str)

    for i in range(len_target):
        target_path_i_path = os.path.join(target_path,target_all_path[i])
        target_df = pd.read_csv(target_path_i_path,encoding="utf-8")

        # Init
        win_str = str(target_all_path[i])
        title_str = "Target Distrb. of "+win_str

        if(i < 50):
            # Hist plot which is not that great
            if viz_env_str == "target_histCDF" :
                viz.histogram(X = np.array(target_df.N), env=viz_env_str, win=win_str,
                            opts= dict(title=title_str,numbins = 50))

            # Line plot
            if viz_env_str == "target_lineCDF" :
                target_df.drop_duplicates(inplace=True)
                viz.line(X = np.array(target_df.N),Y= np.array(target_df.P), env=viz_env_str, win=win_str,opts= dict(title=title_str,markers = True,markersize = 7,markersymbol = "cross-thin-open"))

            # Bar plot. 这个看起来是最准确的一个
            if viz_env_str == "target_barCDF" :
                target_df.drop_duplicates(inplace=True)
                arr_str = [str(i) for i in np.array(target_df.N)]
                viz.bar(X=np.array(target_df.P), env=viz_env_str, win=win_str,
                        opts=dict(title=title_str,rownames=arr_str,stacked = False))

            # Scatter plot
            if viz_env_str == "target_scatterCDF" :
                target_df.drop_duplicates(inplace=True)
                viz.scatter(X=np.array(target_df),env=viz_env_str, win=win_str,opts=dict(title=title_str,markersize = 3))
    print("Done")

# draw_all_target_data_cdf()

- 也是画target data，但是是平滑处理
- `savgol_filter`参数解析:
    - y：代表曲线点坐标（x,y）中的y
    - window_length：窗口长度，该值需为正奇整数。值越小，曲线越贴近真实曲线；值越大，平滑效果越厉害
    - polyorder: 对窗口内的数据点进行k阶多项式拟合，k的值需要小于window_length。值越大，曲线越贴近真实曲线；值越小，平滑效果越厉害
    - mode：确定了要应用滤波器的填充信号的扩展类型。（This determines the type of extension to use for the padded signal to which the filter is applied. ）
- **实际上没用到这个函数**

In [18]:
def draw_smooth_target_data():
    # target data
    target_path = r"../data/targets"
    # target_path里有全部的target data地址
    target_all_path = os.listdir(target_path)
    len_target = len(target_all_path)
    print(f"一共有 *{len_target}* 组 target data")

    # Init
    viz_env_str = "target_bar"
    # viz_env_str = "target_distrb"
    # viz_env_str = "target_hist"
    # viz_env_str = "target_scatter"
    viz = Visdom(env = viz_env_str)

    for i in range(len_target):
        target_path_i_path = os.path.join(target_path,target_all_path[i])
        target_df = pd.read_csv(target_path_i_path,encoding="utf-8")

        # Init
        win_str = str(target_all_path[i])
        title_str = "Target Distrb. of "+win_str

        if(i < 100):
            # Smoothen the data
            y_smooth = scipy.signal.savgol_filter(target_df.P,window_length=53,polyorder=3)
            # y_smooth = scipy.signal.savgol_filter(target_df.P, 99, 1, mode= 'nearest')
            target_df.P = y_smooth

            # Hist plot which is not that great
            # viz.histogram(X = np.array(target_df.N), env=viz_env_str, win=win_str,
            #             opts= dict(title=title_str,numbins = 50))

            # Line plot
            # target_df.drop_duplicates(inplace=True)
            # viz.line(X = np.array(target_df.N),Y= np.array(target_df.P), env=viz_env_str, win=win_str,opts= dict(title=title_str,markers = True,markersize = 7,markersymbol = "cross-thin-open"))

            # Bar plot. 这个看起来是最准确的一个
            target_df.drop_duplicates(inplace=True)
            arr_str = [str(i) for i in np.array(target_df.N)]
            viz.bar(X=np.array(target_df.P), env=viz_env_str, win=win_str,
                    opts=dict(title=title_str,rownames=arr_str))

            # Scatter plot
            # target_df.drop_duplicates(inplace=True)
            # viz.scatter(X=np.array(target_df),env=viz_env_str, win=win_str,opts=dict(title=title_str,markersize = 3))
    print("Done")

# draw_smooth_target_data()

In [19]:
#### Test for drawing
def test_draw():
    viz = Visdom(env=env_str)

    mu = torch.tensor([0,10,20])
    sigma = torch.tensor([1,1,1])
    duration = torch.tensor([0,1,2,0])
    duration = torch.repeat_interleave(duration.unsqueeze(dim=1), repeats=3, dim=1)
    m = torch.distributions.Normal(loc=mu, scale=sigma)
    pi = torch.tensor([0.2,0.3,0.5])

    # draw
    x_0 = torch.tensor(np.arange(0,1000))
    x = torch.repeat_interleave(x_0.unsqueeze(dim=1), repeats=3, dim=1)
    y = torch.exp(m.log_prob(x))
    y_sum = torch.unsqueeze(torch.sum(pi*y,dim=1),dim=1)
    viz.line(X = x_0,Y= torch.cat([y,y_sum],dim = 1), env=env_str, win="test_draw_2",
            opts= dict(title='test_draw', legend=['N1', 'N2', 'N3','NNN']))
# test_draw()

## 5.2 plot mdn

### 5.2.1 mdn pdf的图像[with input data]
1. 求解[1,6,11...]上的cdf：
    - 求解[1,6,11..]的cdf，再求解[6,11,..]，两者相减

In [319]:
# smoothed_y[t] = average(y[t-k], y[t-k+1], ..., y[t+k-1], y[t+k])
# sm表示滑动窗口大小,为2*k+1,
def smooth(data, sm=1):
    if sm > 1:
        smooth_data = []
        for d in data:
            y = np.ones(sm)*1.0/sm
            d = np.convolve(y, d, "same")

            smooth_data.append(d)

    return smooth_data

In [320]:
def draw_mdn_2(pi, mu, sigma, target, input, total_train_step, N_gaussians):
    """
    画两条曲线，pred-1表示归一化前，pred-2表示归一化后

    :param pi:
    :param mu:
    :param sigma:
    :param target:
    :param input:
    :param total_train_step:
    :param opt.N_gaussians:
    :return:
    """
    # 只画一个batch中的第一个

    # The target distrb.
    target = torch.unique(target,dim=0)    # drop the duplicate
    n_target = target[:,0]
    non_zero_idx = torch.nonzero(n_target)
    n = n_target[non_zero_idx]

    p_target = target[:,1]
    p = p_target[non_zero_idx]
    max_n = int(max(n).item())

    # The predicted distrb.
    m = torch.distributions.Normal(mu,sigma)          # Gaussian
    # m = torch.distributions.Laplace(mu,sigma)           # Laplace

    x_0 = torch.arange(1,(max_n+opt.TARGET),opt.TARGET).to(device=device)

    x = torch.repeat_interleave(x_0.unsqueeze(dim=1), repeats=opt.N_gaussians, dim=1)   # expand dim
    # 求解每个长度为TARGET的区间上的cdf
    y = (m.cdf(x+opt.TARGET) - m.cdf(x)).to(device=device)

    # 方法一：
    y_pred_1 = torch.sum(pi*y,dim=1)
    # 方法二：做一下(0,1)上的归一化
    y_pred_2 = y_pred_1/y_pred_1.sum()

    # The input distrb.
    input_data = input[0:2,:]
    x_input = torch.arange(1,(300+1),opt.SCALE).to(device=device)
    y_input_0 = (input_data[0,:]).to(device=device)
    y_input_1 = (input_data[1,:]).to(device=device)

    # Init
    win_str = "total_train_step = "+str(total_train_step)
    title_str = "Distrb. in "+win_str
    viz.line(X = [0.],Y = [0.], env=env_str, win=win_str, opts= dict(title=title_str))

    # Visdom本身不能把hist和line画在一个window中
    # 如果想画一起只能是两条line
    # Plot y_target
    # viz.histogram(X = n, env=env_str, win=win_str,
    #         opts= dict(title=title_str))
    viz.line(X = n,Y= p, env=env_str, win=win_str, update="append", name='target',
            opts= dict(title=title_str,markers = True,markersize = 7,markersymbol = "cross-thin-open"))

    # Plot y_pred
    viz.line(X = x_0,Y= y_pred_1, env=env_str, win=win_str, update="append", name='pred-1',
            opts= dict(title=title_str))

    # Plot y_pred_2
    viz.line(X = x_0,Y= y_pred_2, env=env_str, win=win_str, update="append", name='pred-2',
            opts= dict(title=title_str))

    # Plot y_input
    # 如果input data长度短，全部画完
    if(len(x_input) <= max_n):
        viz.line(X = x_input,Y= y_input_0, env=env_str, win=win_str, update="append", name='GT-1', opts= dict(title=title_str))
        viz.line(X = x_input,Y= y_input_1, env=env_str, win=win_str, update="append", name='GT-2', opts= dict(title=title_str))
    # 如果input data长度长，则截断
    else:
        x_input_0 = x_input[0:max_n]
        y_input_2 = y_input_0[0:max_n]/y_input_0[0:max_n].sum()
        y_input_3 = y_input_1[0:max_n]/y_input_1[0:max_n].sum()
        viz.line(X = x_input_0,Y= y_input_2, env=env_str, win=win_str, update="append", name='GT-1', opts= dict(title=title_str))
        viz.line(X = x_input_0,Y= y_input_3, env=env_str, win=win_str, update="append", name='GT-2', opts= dict(title=title_str))

### 5.2.2 MDN+weibull[with input data]

In [321]:
def draw_mdn_wei(pi, scale, shape, target, input_data, total_train_step, N_gaussians):
    """
    画两条曲线，pred-1表示归一化前，pred-2表示归一化后

    :param pi:
    :param scale:
    :param shape:
    :param target: target data records
    :param input:  为了画图的input，未经过任何处理
    :param total_train_step:
    :param opt.N_gaussians:
    :return:
    """
    # 只画一个batch中的第一个

    # The target distrb.
    target = torch.unique(target,dim=0)    # drop the duplicate
    n_target = target[:,0]
    non_zero_idx = torch.nonzero(n_target)
    n = n_target[non_zero_idx]

    p_target = target[:,1]
    p = p_target[non_zero_idx]
    max_n = int(max(n).item())

    # The predicted distrb.
    m = torch.distributions.Weibull(scale, shape)

    x_0 = torch.arange(1,(max_n+1)).to(device=device)
    x = torch.repeat_interleave(x_0.unsqueeze(dim=1), repeats=N_gaussians, dim=1)   # expand dim
    # 求解每个小区间上的cdf作为likelihood
    y = (m.cdf(x+0.5) - m.cdf(x-0.5)).to(device=device)

    # 方法一：
    y_pred_1 = torch.sum(pi*y,dim=1)
    # 方法二：做一下(0,1)上的归一化
    y_pred_2 = y_pred_1/y_pred_1.sum()

    # The input distrb.
    x_input = torch.arange(1,(300+1),opt.SCALE).to(device=device)
    y_input_0 = torch.flatten(input_data[0,:]).to(device=device)
    y_input_1 = torch.flatten(input_data[2,:]).to(device=device)

    # Init
    win_str = "total_train_step = "+str(total_train_step)
    title_str = "Distrb. in "+win_str
    viz.line(X = [0.],Y = [0.], env=env_str, win=win_str, opts= dict(title=title_str))

    # Visdom本身不能把hist和line画在一个window中
    # 如果想画一起只能是两条line
    # Plot y_target
    # viz.histogram(X = n, env=env_str, win=win_str,
    #         opts= dict(title=title_str))
    viz.line(X = n,Y= p, env=env_str, win=win_str, update="append", name='target',
            opts= dict(title=title_str,markers = True,markersize = 7,markersymbol = "cross-thin-open"))

    # Plot y_pred
    viz.line(X = x_0,Y= y_pred_1, env=env_str, win=win_str, update="append", name='pred-1',
            opts= dict(title=title_str))

    # Plot y_pred_2
    viz.line(X = x_0,Y= y_pred_2, env=env_str, win=win_str, update="append", name='pred-2',
            opts= dict(title=title_str))

    # Plot y_input
    # 如果GT data长度短，全部画完
    if(len(x_input) <= max_n):
        x_input = torch.flatten(x_input)
        viz.line(X = x_input,Y= y_input_0, env=env_str, win=win_str, update="append", name='GT-1', opts= dict(title=title_str))
        viz.line(X = x_input,Y= y_input_1, env=env_str, win=win_str, update="append", name='GT-2', opts= dict(title=title_str))
    # 如果GT data长度长，则截断
    else:
        x_input_0 = torch.flatten(x_input[0:max_n])
        y_input_2 = y_input_0[0:max_n]/y_input_0[0:max_n].sum()
        y_input_3 = y_input_1[0:max_n]/y_input_1[0:max_n].sum()
        viz.line(X = x_input_0,Y= y_input_2, env=env_str, win=win_str, update="append", name='GT-1', opts= dict(title=title_str))
        viz.line(X = x_input_0,Y= y_input_3, env=env_str, win=win_str, update="append", name='GT-2', opts= dict(title=title_str))

## 5.3 png格式的net structure

In [ ]:
def draw_the_net_png():

    x = torch.randn([1, 3, 300])  # 定义网络的输入值
    mlp = MLP_1_1(opt.N_gaussians)
    y = mlp(x)                    # 获取网络的预测值

    MyConvNetVis = make_dot(y, params=dict(list(mlp.named_parameters()) + [('x', x)]))
    MyConvNetVis.format = "png"
    # 指定文件生成的文件夹
    MyConvNetVis.directory = "data_pic"
    # 生成文件
    MyConvNetVis.view()
# draw_the_net_png()

## 5.4 plot the loss
1. 直接根据参数决定draw什么loss，反正loss都画在一个window里面

In [9]:
win_train_loss_str = "The Loss of BATCH in the Training Data"
win_vali_loss_str = "The Loss in the Vali Data"
win_train_epoch_loss_str = "The Loss of EPOCH in the Training Data"

def draw_loss(X_step, loss, win_str):
    viz.line(X = [X_step], Y = [loss],win=win_str, update="append",
        opts= dict(title=win_str))


## 5.5 plot the metric

In [10]:
win_vali_metric_str = "The NLL of ALL vali data"
def draw_metric(X_step, total_vali_metric, GT_metric):

    viz.line(X = [X_step], Y = [[total_vali_metric,GT_metric[0,0],GT_metric[0,1]]],win=win_vali_metric_str, update="append", opts= dict(title=win_vali_metric_str, legend=['pred','GT-1','GT-2(common)'], showlegend=True,xlabel="epoch", ylabel="NLL"))

## 5.6 grad graph
https://github.com/t-vi/pytorch-tvmisc/blob/master/visualize/bad_grad_viz.ipynb

In [11]:

def iter_graph(root, callback):
    queue = [root]
    seen = set()
    while queue:
        # 队头出fn然后判断fn是否seen
        fn = queue.pop()
        if fn in seen:
            continue
        # unseen加入queue，并且继续沿着fn向下递归（DFS？）
        seen.add(fn)
        for next_fn, _ in fn.next_functions:
            # Alert：只有非none的才会加入queue，然后在register_grad里被fn_dict记录下grad_input
            if next_fn is not None:
                queue.append(next_fn)
        callback(fn)

def register_hooks(var):
    fn_dict = {}  # 记录了grad名字和值（grad_input）
    def hook_cb(fn):
        def register_grad(grad_input, grad_output):
            fn_dict[fn] = grad_input
        fn.register_hook(register_grad)

    # 1. 递归注册grad_input
    iter_graph(var.grad_fn, hook_cb)

    # def is_bad_grad(grad_output):
    #     if grad_output is None:
    #         return False
    #     return grad_output.isnan().any() or (grad_output.abs() >= 1e6).any()
    def is_bad_grad(grad_output):
        if grad_output is None:
                return True
        grad_output = grad_output.data
        return grad_output.ne(grad_output).any() or grad_output.gt(1e6).any()

    # 2. graph已经从grad input构建完了，还有grad output的判断以及颜色的选择
    def make_dot():
        node_attr = dict(style='filled',
                        shape='box',
                        align='left',
                        fontsize='12',
                        ranksep='0.1',
                        height='0.2')
        dot = Digraph(node_attr=node_attr, graph_attr=dict(size="12,12"))

        def size_to_str(size):
            return '('+(', ').join(map(str, size))+')'

        def build_graph(fn):
            if hasattr(fn, 'variable'):  # if GradAccumulator
                u = fn.variable
                node_name = 'Variable\n ' + size_to_str(u.size())
                dot.node(str(id(u)), node_name, fillcolor='lightblue')
            else:  # 不是variable属性，白色
                assert fn in fn_dict, fn   # 判断fn在不在fn_dict里面！
                fillcolor = 'white'
                if any(is_bad_grad(gi) for gi in fn_dict[fn]):
                    fillcolor = 'red'
                dot.node(str(id(fn)), str(type(fn).__name__), fillcolor=fillcolor)
            for next_fn, _ in fn.next_functions:
                if next_fn is not None:
                    next_id = id(getattr(next_fn, 'variable', next_fn))
                    dot.edge(str(next_id), str(id(fn)))
        iter_graph(var.grad_fn, build_graph)

        return dot

    return make_dot

# x = torch.randn(10, 10, requires_grad=True)
# y = torch.randn(10, 10, requires_grad=True)
#
# z = x / (y * 0)
# z = z.sum() * 2
# get_dot = register_hooks(z)


# with torch.autograd.detect_anomaly():
#     z.backward()
#     dot = get_dot()
#     dot.save('tmp.dot') # to get .dot
#     dot.render('tmp') # to get SVG
#     # dot # in Jupyter, you can just render the variable

# 6 Training
## 6.1 Init

In [55]:
# torch.autograd.set_detect_anomaly(True)
# mlp = MLP_1_7(opt.N_gaussians)
# (9,3)不错
mlp = Conv_1_4(opt.N_gaussians)
# mlp = Conv_2_1(opt.N_gaussians)
# mlp = Conv_1_7(opt.N_gaussians,kernel_size=9,stride=3)

# Init the params
# mlp = model_param_init(mlp)

# Save the init params
# torch.save(mlp.state_dict(), 'mlp_init.pth')

# Load the saved model
# model_path_WD = "mlp_train=300_WD.pth"
# model_path_init = 'mlp_init.pth'
# model_path_LSE = "mlp_train=300_LSE.pth"
# model_path_MLE = "mlp_train=300_MLE.pth"
#
# model_data = torch.load(model_path_init)
# mlp.load_state_dict(model_data)

mlp = mlp.to(device=device)
summary(mlp, (3,300))

############ learning rate strategy ############
# 1.
# Set different lr for params
# id: id() 函数返回对象的唯一标识符，标识符是一个整数。返回对象的内存地址。
shape_params = list(map(id, mlp.z_shape.parameters()))
scale_params = list(map(id, mlp.z_scale.parameters()))
pi_params = list(map(id, mlp.z_pi.parameters()))


params_id = shape_params + scale_params + pi_params

base_params = filter(lambda p: id(p) not in params_id, mlp.parameters())
params = [{'params': base_params},         # 如果对某个参数不指定学习率，就使用最外层的默认学习率
          {'params': mlp.z_pi.parameters(), 'lr': opt.lr_for_pi},
        {'params': mlp.z_shape.parameters(), 'lr': opt.lr_for_shape},
          {'params': mlp.z_scale.parameters(), 'lr': opt.lr_for_scale}]

optimizer = torch.optim.AdamW(params, lr=1e-3,weight_decay=opt.weight_decay)

# warmup_scheduler = warmup.ExponentialWarmup(optimizer, warmup_period=10)
# 2.
# Or set lr decay
# StepLR为步进，每step_size个epoch，lr*gamma
scheduler  = torch.optim.lr_scheduler.StepLR(optimizer,step_size=15,gamma=opt.StepLR_gamma) # opt.StepLR_step_size
# scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max = 70, eta_min = 1e-7)
# scheduler = torch.optim.lr_scheduler.ExponentialLR(optimizer, 0.98, last_epoch=-1)
# scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(optimizer, mode='min', factor=0.7, patience=5, verbose=False, threshold=1e-3, threshold_mode='abs', cooldown=0, min_lr=1e-7, eps=1e-7)
# threshold:只关注超过阈值的显著变化；cooldown：触发一次条件后，等待一定epoch再进行检测，避免lr下降过速；

# # Set the hooks
# #mlp.conv1.register_forward_hook(hook_forward_fn)
# mlp.conv1.register_full_backward_hook(hook_backward_fn)
#
# #mlp.linear1.register_forward_hook(hook_forward_fn)
# #mlp.linear1.register_full_backward_hook(hook_backward_fn)
#
# #mlp.z_pi.register_forward_hook(hook_forward_fn)
# mlp.z_pi.register_full_backward_hook(hook_backward_fn_pi)
#
# #mlp.z_mu.register_forward_hook(hook_forward_fn)
# mlp.z_mu.register_full_backward_hook(hook_backward_fn_mu)
#
# mlp.z_sigma.register_forward_hook(hook_forward_fn)
# mlp.z_sigma.register_full_[2, 3, 300]backward_hook(hook_backward_fn_sigma)

----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
       BatchNorm1d-1               [-1, 3, 300]               6
            Conv2d-2             [-1, 1, 1, 98]              28
       BatchNorm1d-3                   [-1, 98]             196
          Softplus-4                   [-1, 98]               0
      Conv_block_4-5                   [-1, 98]               0
            Conv2d-6             [-1, 1, 1, 98]              28
       BatchNorm1d-7                   [-1, 98]             196
          Softplus-8                   [-1, 98]               0
      Conv_block_4-9                   [-1, 98]               0
           Conv2d-10             [-1, 1, 1, 98]              28
      BatchNorm1d-11                   [-1, 98]             196
         Softplus-12                   [-1, 98]               0
     Conv_block_4-13                   [-1, 98]               0
           Linear-14                   

In [56]:
writer = SummaryWriter(log_dir="logs-MLP/"+opt.logs_str,flush_secs=60)

# Init the vis win
viz.line(X = [0.],Y = [0.], env=env_str, win=win_train_loss_str, opts= dict(title=win_train_loss_str))
viz.line(X = [0.],Y = [0.], env=env_str, win=win_train_epoch_loss_str, opts= dict(title=win_train_epoch_loss_str))
viz.line(X = [0.],Y = [[0.,0.,0.]], env=env_str, win=win_vali_metric_str, opts= dict(title=win_vali_metric_str,legend=['pred','GT-1','GT-2'], showlegend=True,xlabel="epoch", ylabel="NLL"))

# mlp.eval()
# with torch.no_grad():
#     total_vali_metric, GT_metric,_ = validate(mlp,val_loader,opt.N_gaussians, opt.MIN_LOSS,device)
#     draw_metric(0, total_vali_metric.cpu(), GT_metric)
plot_net(writer,mlp,torch.randn((2,3,300),device=device))
print("Done")

Done


## 6.2 grad check


In [57]:
# # grad check
# input_test = torch.randn((2,3,300), requires_grad=True,device=device)
# test_ans = gradcheck(mlp.to(device), input_test, eps=1e-3)  #, eps=1e-6, atol=1e-4
# print("Are the gradients correct: ", test_ans)

## 6.3 START HERE


In [58]:
# filename = "../log_file.txt"
# f = open(filename,'w')
total_train_step = 0

mlp.train()

for epoch in range(opt.EPOCH_NUM):
    # # Save the net structure
    # net_file_name = "net_before_epoch"+str(epoch)+".pth"
    # net_path = opt.net_root_path + net_file_name
    # torch.save(mlp.state_dict(), net_path)

    epoch_train_loss = 0
    # plot_conv(writer,mlp,epoch)
    print(f"========== Now this is EPOCH {epoch} ,lr is {scheduler.get_last_lr()}==========")
    for batch_id,data in enumerate(train_loader):

        input_data, target_plot, target_loss, setting, _ = data
        # print(f"---- {batch_id} batch----")
        # Do the inference
        input_data = input_data.to(device)
        target_loss = target_loss.to(device)
        target_plot = target_plot.to(device)

        # with autocast():
        pi, mu, sigma = mlp(input_data)

        # Cal the MLE loss and draw the distrb.
        # loss = loss_fn_v2(pi, mu, sigma, target_loss, opt.N_gaussians,opt.TARGET, opt.SAFETY, device)
        loss = loss_fn_wei(pi, mu, sigma, target_loss, opt.N_gaussians,opt.TARGET, opt.SAFETY, device)
        # loss = loss_fn_v3(pi, mu, sigma, target_loss, opt.N_gaussians,device)
        # loss = loss_fn_v5(pi, mu, sigma, target_loss, opt.N_gaussians,device)
        # optimizer.zero_grad()
        # 如果unscale_()没有被明确调用，梯度将在step()过程中被自动取消缩放。
        # scaler.unscale_(optimizer)
        # torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm)
        # scaler.scale(loss).backward()
        # scaler.step(optimizer)
        # scaler.update()
        # Cal the CDF loss and draw the distrb.
        # loss = loss_fn_cdf(pi, mu, sigma, target, opt.N_gaussians)

        # Cal the CE or KL loss and draw the distrb.
        # loss  = loss_fn_CE(pi, mu, sigma, target_loss, opt.N_gaussians,opt.TARGET, opt.SAFETY, device)

        # Cal the WD loss and draw the distrb.
        # loss  = loss_fn_WD(pi, mu, sigma, target_loss, opt.N_gaussians,opt.TARGET,device)

        epoch_train_loss += loss.detach().cpu()
        draw_loss(total_train_step, loss.item(),win_train_loss_str)

        # Optim
        optimizer.zero_grad()
        loss.backward()

        ########### before step() ###############

        # for name, parms in mlp.named_parameters():
        #     print("=====before step()=====")
        #     print('-->name:', name)
        #     print('-->params:', parms.data)
        #     # print('-->grad_requirs:',parms.requires_grad)
        #     print('-->grad_value:',parms.grad)
        #     print("===")

        ######

        # 反向传播时检测是否有异常值，定位code
        # with torch.autograd.detect_anomaly():
        #     loss.backward()

        ######
        # get_dot = register_hooks(loss)
        # dot = get_dot()
        # dot.save('tmp.dot')   # to get .dot
        # dot.render('tmp')     # to get pdf

        ######
        # Print grad check
        # v_n = []    # name
        # v_v = []    # value
        # v_g = []    # grad
        # for name, parameter in mlp.named_parameters():
        #     v_n.append(name)
        #     v_v.append(parameter.detach().cpu().numpy() if parameter is not None else [0])
        #     v_g.append(parameter.grad.detach().cpu().numpy() if parameter.grad is not None else [0])
        # for i in range(len(v_n)):
        #     # if np.max(v_v[i]).item() - np.min(v_v[i]).item() < 1e-6:
        #     #     color = bcolors.FAIL + '*'
        #     if np.isnan(v_g[i]).any() or np.isnan(v_v[i]).any():
        #         color = bcolors.FAIL + '*'
        #     else:
        #         color = bcolors.OKGREEN + ' '
        #     print('%svalue %s: %.3e ~ %.3e' % (color, v_n[i], np.min(v_v[i]).item(), np.max(v_v[i]).item()))
        #     print('%sgrad  %s: %.3e ~ %.3e' % (color, v_n[i], np.min(v_g[i]).item(), np.max(v_g[i]).item()))

        ######
        clip_grad_norm_(mlp.parameters(), max_norm=20, norm_type=2)#使用第二种裁剪方式
        optimizer.step()

        # for name, parms in mlp.named_parameters():
        #     print("=====After step()=====")
        #     print('-->name:', name)
        #     print('-->params:', parms.data)
        #     # print('-->grad_requirs:',parms.requires_grad)
        #     print('-->grad_value:',parms.grad)
        #     print("===")

        # Only draw the 1st result in a training batch (5 in total)
        # if total_train_step % 20 == 0:
        #     with torch.no_grad():
        #         # draw_mdn_2(pi[0,:].clone().detach(), mu[0,:].clone().detach(), sigma[0,:].clone().detach(), target_plot[0].clone().detach(), input_data[0].clone().detach(),total_train_step, opt.N_gaussians)
        #         draw_mdn_wei(pi[0,:].clone().detach(), mu[0,:].clone().detach(), sigma[0,:].clone().detach(), target_plot[0].clone().detach(), input_data[0].clone().detach(),total_train_step, opt.N_gaussians)
        #         # draw_mdn_cdf(pi[0,:].detach(), m[0], target[0].detach(), total_train_step, loss_list[0],opt.N_gaussians)
        total_train_step += 1

    ########### Do validation

    # mlp.eval()
    # with torch.no_grad():
    #     total_vali_metric, GT_metric, odds = validate(mlp,val_loader,opt.N_gaussians, opt.MIN_LOSS,device)
    #     draw_metric(epoch+1, total_vali_metric.cpu(), GT_metric)
    #     # writer.add_scalars("metric/"+opt.tag_str,{"pred":total_vali_metric.cpu(),
    #     #                              "GT-1":GT_metric[0,0],
    #     #                              "GT-2":GT_metric[0,1]},epoch)
    # mlp.train()

    # Plot the loss in this EPOCH
    print(f"========== IN EPOCH {epoch} the total loss is {epoch_train_loss} ==========")
    # print(f"========== IN EPOCH {epoch} the vali NLL loss is {total_vali_metric.detach().cpu().numpy()} ==========")
    # print(f"========== IN EPOCH {epoch} the GT metric is {GT_metric.detach().cpu().numpy()} ==========")
    # print(f"========== IN Test dataset, the odds:  {odds} ==========")

    # # Save the net structure
    # net_file_name = "net_after_epoch"+str(epoch)+".pth"
    # net_path = opt.net_root_path + net_file_name
    # torch.save(mlp.state_dict(), net_path)

    # Plot loss of this EPOCH
    draw_loss(epoch, epoch_train_loss,win_train_epoch_loss_str)
    # writer.add_scalars("Loss of EPOCH",{"Train":epoch_train_loss},epoch)
    # scheduler.step(total_vali_metric)
    scheduler.step()

    if epoch%1==0:
        # Record the weight
        plot_conv_weight(writer,mlp,epoch,opt.tag_str)
        plot_mu_weight(writer,mlp,epoch,opt.tag_str)
        plot_pi_weight(writer,mlp,epoch,opt.tag_str)
        plot_sigma_weight(writer,mlp,epoch,opt.tag_str)

# f.close()

# writer.close()
print("Done")

========== Now this is EPOCH 0 ,lr is [0.001, 0.005, 0.005, 0.005]==========
========== IN EPOCH 0 the total loss is 17754.56640625 ==========
========== IN EPOCH 0 the vali NLL loss is 2.043644905090332 ==========
========== IN EPOCH 0 the GT metric is [[7.263021  9.906305  8.764881  7.4794397]] ==========
========== IN Test dataset, the odds:  [0.0, 0.0, 0.0] ==========
========== Now this is EPOCH 1 ,lr is [0.001, 0.005, 0.005, 0.005]==========
========== IN EPOCH 1 the total loss is 12047.1318359375 ==========
========== IN EPOCH 1 the vali NLL loss is 1.9566820859909058 ==========
========== IN EPOCH 1 the GT metric is [[7.263021  9.906305  8.764881  7.4794393]] ==========
========== IN Test dataset, the odds:  [0.0, 0.0, 0.0] ==========
========== Now this is EPOCH 2 ,lr is [0.001, 0.005, 0.005, 0.005]==========


KeyboardInterrupt: 

- test

In [27]:
mlp.eval()
with torch.no_grad():
    total_test_metric, GT_metric, odds = validate(mlp,test_loader,opt.N_gaussians, opt.MIN_LOSS,device)
    # writer.add_scalars("metric/"+opt.tag_str,{"pred":total_vali_metric.cpu(),
    #                              "GT-1":GT_metric[0,0],
    #                              "GT-2":GT_metric[0,1]},epoch)
    print("total_test_metric:",total_test_metric)
    print("GT_metric:",GT_metric)
mlp.train()

total_test_metric: tensor(6.4932, device='cuda:0')
GT_metric: tensor([[6.9811, 9.3606, 8.2965, 7.0679]])


Conv_1_4(
  (BN1): BatchNorm1d(3, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (layer_pi): Conv_block_4(
    (ac_func): Softplus(beta=1, threshold=20)
    (conv): Conv2d(1, 1, kernel_size=(3, 9), stride=(3, 3))
    (BN_aff2): BatchNorm1d(98, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  )
  (layer_scale): Conv_block_4(
    (ac_func): Softplus(beta=1, threshold=20)
    (conv): Conv2d(1, 1, kernel_size=(3, 9), stride=(3, 3))
    (BN_aff2): BatchNorm1d(98, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  )
  (layer_shape): Conv_block_4(
    (ac_func): Softplus(beta=1, threshold=20)
    (conv): Conv2d(1, 1, kernel_size=(3, 9), stride=(3, 3))
    (BN_aff2): BatchNorm1d(98, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  )
  (ac_func): Softplus(beta=1, threshold=20)
  (z_pi): Sequential(
    (0): Linear(in_features=98, out_features=2, bias=True)
    (1): Softmax(dim=1)
  )
  (z_scale): Linear(in_features=98, out_feat

In [65]:
model_path_MLP = "mlp_train=300_MLP.pth"
model_path_Conv = "mlp_train=300_Conv.pth"
model_path_LSE = "mlp_train=300_LSE.pth"
torch.save(mlp.state_dict(), model_path_Conv)
# torch.save(mlp.state_dict(), model_path_MLE)

# viz.delete_env("001_test")

## 6.4 retrain
1. 固定参数，retrain scale和pi

In [1099]:
def freeze_model(model):

    for (name, param) in model.named_parameters():
        if "pi" in name:
            pass
        else:
            param.requires_grad = False

    # # 打印当前的固定情况（可忽略）：
    # freezed_num, pass_num = 0, 0
    # for (name, param) in model.named_parameters():
    #     if param.requires_grad == False:
    #         freezed_num += 1
    #     else:
    #         pass_num += 1
    # print('\n Total {} params, miss {} \n'.format(freezed_num + pass_num, pass_num))

    return model

mlp_2 = Conv_1_4(opt.N_gaussians,kernel_size=9,stride=3)
# 获取要固定部分的state_dict:
model_data = torch.load(model_path_Conv, map_location=device)
mlp_2.load_state_dict(model_data, strict=False)
# 固定部分网络参数:
model = freeze_model(model=mlp_2)
model.to(device)
optimizer = torch.optim.AdamW(filter(lambda p: p.requires_grad, model.parameters()), lr=1e-4,weight_decay=opt.weight_decay)
scheduler  = torch.optim.lr_scheduler.StepLR(optimizer,step_size=opt.StepLR_step_size,gamma=opt.StepLR_gamma)
# scheduler = torch.optim.lr_scheduler.ExponentialLR(optimizer, 0.95, last_epoch=-1)


In [1100]:
writer = SummaryWriter(log_dir="logs-MLP/"+opt.logs_str,flush_secs=60)

# Init the vis win
viz.line(X = [0.],Y = [0.], env=env_str, win=win_train_loss_str, opts= dict(title=win_train_loss_str))
viz.line(X = [0.],Y = [0.], env=env_str, win=win_train_epoch_loss_str, opts= dict(title=win_train_epoch_loss_str))
viz.line(X = [0.],Y = [[0.,0.,0.]], env=env_str, win=win_vali_metric_str, opts= dict(title=win_vali_metric_str,legend=['pred','GT-1','GT-2'], showlegend=True,xlabel="epoch", ylabel="NLL"))

model.eval()
with torch.no_grad():
    total_vali_metric, GT_metric = validate(model,val_loader,opt.N_gaussians, opt.MIN_LOSS,device)
    draw_metric(0, total_vali_metric.cpu(), GT_metric)
print("Done")

Done


In [1101]:
total_train_step = 0
EPOCH_NUM = 30

train_start_time = time.time()
model.train()

for epoch in range(EPOCH_NUM):
    # # Save the net structure
    # net_file_name = "net_before_epoch"+str(epoch)+".pth"
    # net_path = opt.net_root_path + net_file_name
    # torch.save(mlp.state_dict(), net_path)

    epoch_train_loss = 0
    # plot_conv(writer,mlp,epoch)
    print(f"========== Now this is EPOCH {epoch} ,lr is {scheduler.get_last_lr()}==========")
    for batch_id,data in enumerate(train_loader):

        input_data, target_plot, target_loss, setting, _ = data
        # Do the inference
        input_data = input_data.to(device)
        target_loss = target_loss.to(device)
        target_plot = target_plot.to(device)
        pi, mu, sigma = model(input_data)

        # Cal the MLE loss and draw the distrb.
        # loss = loss_fn_v2(pi, mu, sigma, target_loss, opt.N_gaussians,opt.TARGET, opt.SAFETY, device)
        # loss = loss_fn_wei(pi, mu, sigma, target_loss, opt.N_gaussians,opt.TARGET, opt.SAFETY, device)
        # loss = loss_fn_v3(pi, mu, sigma, target_loss, opt.N_gaussians,device)
        # loss = loss_fn_v5(pi, mu, sigma, target_loss, opt.N_gaussians,device)

        # Cal the CDF loss and draw the distrb.
        # loss = loss_fn_cdf(pi, mu, sigma, target, opt.N_gaussians)

        # Cal the CE or KL loss and draw the distrb.
        # loss  = loss_fn_CE(pi, mu, sigma, target_loss, opt.N_gaussians,opt.TARGET, opt.SAFETY, device)

        # Cal the WD loss and draw the distrb.
        # loss  = loss_fn_WD(pi, mu, sigma, target_loss, opt.N_gaussians,opt.TARGET,device)

        # loss  = loss_fn_mse(pi, mu, sigma, target_loss, opt.N_gaussians,opt.TARGET, opt.SAFETY, device)
        epoch_train_loss += loss.item()
        draw_loss(total_train_step, loss.item(),win_train_loss_str)

        # Optim
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        total_train_step += 1

    ########### Do validation

    model.eval()
    with torch.no_grad():
        total_vali_metric, GT_metric = validate(model,val_loader,opt.N_gaussians, opt.MIN_LOSS,device)
        draw_metric(epoch+1, total_vali_metric.cpu(), GT_metric)
        writer.add_scalars("metric/"+opt.tag_str,{"pred":total_vali_metric.cpu(),
                                     "GT-1":GT_metric[0,0],
                                     "GT-2":GT_metric[0,1]},epoch)
    model.train()

    # Plot the loss in this EPOCH
    print(f"========== IN EPOCH {epoch} the total loss is {epoch_train_loss} ==========")
    print(f"========== IN EPOCH {epoch} the vali NLL loss is {total_vali_metric.detach().cpu().numpy()} ==========")
    print(f"========== IN EPOCH {epoch} the GT metric is {GT_metric.detach().cpu().numpy()} ==========")

    # Plot loss of this EPOCH
    draw_loss(epoch, epoch_train_loss,win_train_epoch_loss_str)
    # writer.add_scalars("Loss of EPOCH",{"Train":epoch_train_loss},epoch)
    # scheduler.step(total_vali_metric)
    scheduler.step()

train_end_time = time.time()
print(f"Total training time when epoch= *{EPOCH_NUM}* is *{train_end_time-train_start_time} *s")
writer.close()
print("Done")

========== Now this is EPOCH 0 ,lr is [0.0001]==========


RuntimeError: Trying to backward through the graph a second time (or directly access saved tensors after they have already been freed). Saved intermediate values of the graph are freed when you call .backward() or autograd.grad(). Specify retain_graph=True if you need to backward through the graph a second time or if you need to access saved tensors after calling backward.


$\mathcal{L}(y \vert x) = - \log\bigg\{\sum_{k=1}^K \pi_k(x)  \mathcal{N}\big(y \vert \mu_k(x), \Sigma_k(x)\big)\bigg\}$

# 7. Load and test
## 7.1 load and init

In [17]:
Model_name = opt.net_root_path

model_path_MLP = "mlp_train=300_MLP.pth"
model_path_Conv = "mlp_train=300_Conv.pth"
model_path_init = "mlp_init.pth"

mlp = Conv_1_4(opt.N_gaussians)

model_data = torch.load(Model_name)
mlp.load_state_dict(model_data)

mlp = mlp.to(device=device)

In [18]:
plot_conv_weight(writer,mlp,0,opt.tag_str)
plot_mu_weight(writer,mlp,0,opt.tag_str)
plot_pi_weight(writer,mlp,0,opt.tag_str)
plot_sigma_weight(writer,mlp,0,opt.tag_str)

import seaborn as sns
import torch.nn as nn

# 定义卷积层
conv1 = nn.Conv2d(in_channels=3, out_channels=32, kernel_size=3, stride=1, padding=1)

# 获取权重数据并转换为numpy数组
weights = conv1.weight.data.cpu().numpy()

# 可视化权重数据
sns.set(style="white", context="talk")
fig, ax = plt.subplots(figsize=(15, 8))
sns.heatmap(weights, ax=ax, cmap='YlGnBu')
plt.show()

<IPython.core.display.Javascript object>

ValueError: Must pass 2-d input. shape=(32, 3, 3, 3)

- 计算metric

In [23]:

win_pi_str = "pi distrb-"+Model_name
win_mu_str = "mu distrb-"+Model_name
win_sigma_str = "sigma distrb-"+Model_name

win_scale_str = "scale distrb-"+Model_name
win_shape_str = "shape distrb-"+Model_name

In [439]:
def plot_scatter(viz,data, win_str, ylabel):
    for i in range(len(data)):
         # scatter的input shape：N*2或N*3的
        viz.scatter(X = np.array([[i],[data[i,0].numpy().item()]]).reshape(1,2), env=env_str,win=win_str, opts= dict(title=win_str, xlabel="idx", ylabel=ylabel,markercolor = np.array([0])),update="append")   # 白色
        viz.scatter(X = np.array([[i],[data[i,1].numpy().item()]]).reshape(1,2), env=env_str,win=win_str, opts= dict(title=win_str, xlabel="idx", ylabel=ylabel,markercolor = np.array([255])),update="append") # 蓝色
        # viz.scatter(X = np.array([[i],[data[i,2].numpy().item()]]).reshape(1,2), env=env_str,win=win_str, opts= dict(title=win_str, xlabel="idx", ylabel=ylabel),update="append")

        # viz.scatter(X = np.array([[i],[data[i].numpy().item()]]).reshape(1,2), env=env_str,win=win_str, opts= dict(title=win_str, xlabel="idx", ylabel=ylabel),update="append")

    print("Done: "+win_str)

In [34]:
mlp.eval()
with torch.no_grad():
    #Compute the metric
    total_test_metric, GT_metric,odds = validate(mlp, test_loader, opt.N_gaussians, opt.MIN_LOSS,device,detail = True)
    print(f"========== IN Test dataset, NN Model:  {total_test_metric.detach().cpu().numpy()} ==========")
    print(f"========== IN Test dataset, the GTs: {GT_metric.detach().cpu().numpy()} ==========")
    print(f"========== The diff: {GT_metric.detach().cpu().numpy()[0,0] - total_test_metric.detach().cpu().numpy()} ==========")
    print(f"========== IN Test dataset, the odds:  {odds} ==========")

    # Save pi and mu sigma
    cnt = 0
    pi = torch.tensor([])
    mu = torch.tensor([])
    sigma = torch.tensor([])
    for test_batch_id, test_data in enumerate(test_loader):
        test_input_data, test_target, _, test_setting , test_metric = test_data
        test_input_data = test_input_data.to(device)
        test_target = test_target.to(device)
        cnt = cnt + len(test_input_data)
        test_pi, test_mu, test_sigma = mlp(test_input_data)

        pi = torch.cat([pi,test_pi.detach().cpu()],dim=0)
        mu = torch.cat([mu,test_mu.detach().cpu()],dim=0)
        sigma = torch.cat([sigma,test_sigma.detach().cpu()],dim=0)

========== IN Test dataset, NN Model:  6.225255966186523 ==========
========== IN Test dataset, the GTs: [[ 6.831542  8.726684 13.469078 -6.637537 -1.895143]] ==========
========== The diff: 0.6062860488891602 ==========
========== IN Test dataset, the odds:  [0.5038167938931297, 0.7862595419847328, 0.7862595419847328] ==========


In [441]:
# plot_scatter(viz,mu,win_mu_str,"mu")
# plot_scatter(viz,sigma,win_sigma_str,"sigma")
# plot_scatter(viz,pi,win_pi_str,"pi")

# White: GT-1,Blue: GT-2
plot_scatter(viz,mu,win_scale_str,"scale")
plot_scatter(viz,sigma,win_shape_str,"shape")
plot_scatter(viz,pi,win_pi_str,"pi")

Done: scale distrb-Conv4_N_g=2
Done: shape distrb-Conv4_N_g=2
Done: pi distrb-Conv4_N_g=2


- 研究下pi

In [328]:
pi_df = pd.DataFrame(pi.detach().cpu())
pi_df["pi_GT2_gt_GT1"] = pi_df.iloc[:,1] - pi_df.iloc[:,0]
pi_test = pi_df[pi_df.pi_GT2_gt_GT1>=0]     # 只取出那些GT-2的pi占比比GT-1多的
idx_list = pi_test.index.tolist()   # idx_list对应的是pi shape scale的输出顺序（batchsize = 1）

# reset放在idx_list之后！不要sort！
pi_test.reset_index(inplace=True,drop=False)
pi_test.columns = ['idx_pi_df','GT1_pi','GT2_pi','pi_GT2_gt_GT1']

print(f"GT-2的pi value > GT-1的个数: {idx_list.__len__()}")

GT-2的pi value > GT-1的个数: 84


In [329]:
# 得到这些text data的file idx, 注意不要sort！会破坏和pi的对应关系
idx_testfile = test_idx[idx_list].tolist()

# 读入metric data
metric_df = pd.read_csv(opt.NLL_metric_path,encoding="utf-8")
metric_test = metric_df.iloc[idx_testfile,:]
metric_test.reset_index(inplace=True,drop=False)    # index列对应的是data key idx
metric_test.loc[:,'nll_GT2_minus_GT1'] = metric_test.iloc[:,2]- metric_test.iloc[:,1]

metric_pi_df = pd.concat([metric_test,pi_test],axis = 1)
metric_pi_df.rename(columns={'index':'idx_file'},inplace=True)
metric_pi_df.head()

C:\Users\Administrator\AppData\Local\Temp\ipykernel_22828\430390007.py:8: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



idx_file      nll1       nll2  nll_GT2_minus_GT1  idx_pi_df    GT1_pi  \
0      1200  4.536787   4.702105           0.165318          1  0.437693   
1      1064  5.665173   6.955952           1.290780          2  0.431081   
2      1096  5.457160   5.945142           0.487983          3  0.422328   
3       359  4.992666   5.322161           0.329496          8  0.383956   
4       183  9.338541  21.274504          11.935963          9  0.419274   

     GT2_pi  pi_GT2_gt_GT1  
0  0.562307       0.124614  
1  0.568919       0.137838  
2  0.577672       0.155344  
3  0.616044       0.232088  
4  0.580726       0.161452

- 读入idx_testfile里的test data，画图

In [444]:
dataset_test = myDataset(opt.train_path, opt.target_path_metric, opt.target_path_loss, opt.data_key_path, opt.NLL_metric_path)

# metric_pi_df.shape[0]
mlp.eval()
for i in range(40,50):
    # for test_loader
    idx_file = test_idx[i]                            # 得到test file的idx
    # idx_file = metric_pi_df.loc[i,'idx_file']       # 得到test file的idx
    train_data, target_data ,_, settings_data, metric_df = dataset_test.__getitem__(idx_file)
    input = torch.FloatTensor(train_data).to(device)
    d, b, v, flg_fixedprice = settings_data   # bidincrement,bidfee,retail,flg_fixedprice

    # 给GT-1和GT-2画图，通过target_data得到U和P，从而画图
    duration = target_data[:,0]
    duration_max = max(duration)

    LEN, T = get_LEN_T(v, b, d, duration_max)

    U_1 = get_U_GT1(LEN, v, d, b,eps = 0.)
    U_2 = get_U_GT2(LEN, v, d, b,eps = 0.)

    P_1 = get_P(U_1,LEN)
    # P_1 = P_1/P_1.sum()
    P_2 = get_P(U_2,LEN)
    # P_2 = P_2/P_2.sum()

    # 得到分布
    pi_idx, scale_idx, shape_idx = mlp(input.unsqueeze(0))

    # idx_pi_df = metric_pi_df.loc[i,'idx_pi_df']  # 得到pi等model预测输出的idx
    # # 根据pi shape scale，画出weibull distrb.
    # pi_idx = pi[idx_pi_df,:].to(device=device)
    # scale_idx = mu[idx_pi_df,:].to(device=device)
    # shape_idx = sigma[idx_pi_df,:].to(device=device)

    # 计算nll
    nll = cal_metric(pi_idx.unsqueeze(0), scale_idx.unsqueeze(0), shape_idx.unsqueeze(0), torch.tensor(target_data).unsqueeze(0), opt.N_gaussians, settings_data, opt.MIN_LOSS, device)

    target_nonzero = np.expand_dims(duration,axis=1)
    target_LEN = np.expand_dims(np.arange(1,LEN+1),axis=1)
    # target_LEN or target_nonzero
    target_nonzero_2 = torch.tensor(target_nonzero.repeat(2,1)).to(device=device)

    m = torch.distributions.Weibull(scale_idx,shape_idx)

    loss_1 = (m.cdf(target_nonzero_2 + 0.5) - m.cdf(target_nonzero_2 - 0.5)).to(device=device)
    prob_pred = torch.sum(loss_1 * pi_idx, dim=1)
    prob_pred_np = prob_pred.detach().cpu().numpy()
    # prob_pred_np = prob_pred_np/prob_pred_np.sum()      # NORMA

    #####
    hist_trace = go.Histogram(x=duration, nbinsx=300, histnorm='probability',name='target')
    x_prob = np.arange(1,LEN+1)
    line_trace = go.Scatter(x=duration, y=prob_pred_np, name='pred')
    line_trace_2 = go.Scatter(x=x_prob, y=P_1, name='GT-1')
    line_trace_3 = go.Scatter(x=x_prob, y=P_2, name='GT-2')

    # Create a layout
    layout = go.Layout(title=f'GT = {metric_df} | NN = {nll}', xaxis=dict(title='duration'), yaxis=dict(title='density'))
    # Combine the traces into a single figure
    fig = go.Figure(data=[hist_trace, line_trace,line_trace_2,line_trace_3], layout=layout)
    # Show the figure
    plot_html = fig.to_html(full_html=False)

    fig.show()


## 7.2 fixed-price or asc-price


In [134]:
# 读取所有data key
settings_small_NN_path = r"../data/small_settings_NN.csv"
settings_large_NN_path = r'E:\DATA\large_dta\large_settings_NN.csv'
data_key_small = pd.read_csv(settings_small_NN_path,encoding="utf-8")
data_key_large = pd.read_csv(settings_large_NN_path,encoding="utf-8")
data_key = pd.concat([data_key_small,data_key_large],axis=0,ignore_index=True)
data_key.head()

desc  bidincrement  bidfee  \
0  Sony Ericsson S500i Unlocked Mysterious Green          0.15    0.75   
1               PSP Slim & Lite Sony Piano Black          0.15    0.75   
2     iPod Touch Apple 8GB with Software Upgrade          0.15    0.75   
3                 LG KU990 Viewty Unlocked Black          0.00    0.75   
4      Logitech Cordless Wave Keyboard and Mouse          0.15    0.75   

   retail  flg_fixedprice  
0  499.99               0  
1  169.99               0  
2  299.99               0  
3  899.99               1  
4   89.99               0

In [454]:
# 提取testset中fixed和asc的idx
data_key_test = data_key.iloc[test_idx.tolist(),:].copy()
data_key_test.reset_index(inplace=True)

tmp_1 = data_key_test[data_key_test.flg_fixedprice==1].loc[:,'index']
test_idx_fixed = tmp_1.tolist()

tmp_2 = data_key_test[data_key_test.flg_fixedprice==0].loc[:,'index']
test_idx_asc = tmp_2.tolist()
print(f"fixed-price 在test set中占 {len(test_idx_fixed)/len(test_idx)}, 大小为 {len(test_idx_fixed)}")
print(f"asc - price 在test set中占 {len(test_idx_asc)/len(test_idx)}，, 大小为 {len(test_idx_asc)}")

fixed-price 在test set中占 0.022900763358778626, 大小为 3
asc - price 在test set中占 0.9770992366412213，, 大小为 128


In [451]:
# 提取training set中fixed和asx的idx
data_key_test = data_key.iloc[train_idx.tolist(),:].copy()
data_key_test.reset_index(inplace=True)

tmp_1 = data_key_test[data_key_test.flg_fixedprice==1].loc[:,'index']
train_idx_fixed = tmp_1.tolist()

tmp_2 = data_key_test[data_key_test.flg_fixedprice==0].loc[:,'index']
train_idx_asc = tmp_2.tolist()
print(f"fixed-price 在train set中占 {len(train_idx_fixed)/len(test_idx)}, 大小为 {len(train_idx_fixed)}")
print(f"asc - price 在train set中占 {len(train_idx_asc)/len(test_idx)}，, 大小为 {len(train_idx_asc)}")

fixed-price 在train set中占 0.16793893129770993, 大小为 22
asc - price 在train set中占 6.809160305343512，, 大小为 892


In [455]:
# 给fixed-price和asc分别设置test_loader:
test_loader_fixed = DataLoader(dataset = dataset,batch_size = 1, shuffle=False, num_workers=0, drop_last=False, sampler=SubsetRandomSampler(test_idx_fixed),collate_fn = my_collate_fn_3)
test_loader_asc = DataLoader(dataset = dataset,batch_size = 1, shuffle=False, num_workers=0, drop_last=False, sampler=SubsetRandomSampler(test_idx_asc),collate_fn = my_collate_fn_3)

In [456]:
# ASC
mlp.eval()
with torch.no_grad():
    #Compute the metric
    total_test_metric, GT_metric = validate(mlp,test_loader_asc,opt.N_gaussians, opt.MIN_LOSS,device)
    draw_metric(0, total_test_metric.cpu(), GT_metric)
    print(f"========== IN Test dataset, NN Model + ASC:  {total_test_metric.detach().cpu().numpy()} ==========")
    print(f"========== IN Test dataset, the GTs + ASC: {GT_metric.detach().cpu().numpy()} ==========")
    print(f"========== The diff + ASC: {GT_metric.detach().cpu().numpy()[0,0] - total_test_metric.detach().cpu().numpy()} ==========")

    # Save pi and mu sigma
    cnt = 0
    pi = torch.tensor([])
    mu = torch.tensor([])
    sigma = torch.tensor([])
    for test_batch_id, test_data in enumerate(test_loader_asc):
        test_input_data, test_target, _, test_setting , test_metric = test_data
        test_input_data = test_input_data.to(device)
        test_target = test_target.to(device)
        cnt = cnt + len(test_input_data)
        test_pi, test_mu, test_sigma = mlp(test_input_data)

        # draw_mdn_wei(test_pi[1,:].clone().detach(), test_mu[1,:].clone().detach(), test_sigma[1,:].clone().detach(), test_target[1].clone().detach(), test_input_data[1].clone().detach(),-(test_batch_id+101), opt.N_gaussians)
        # draw_mdn_wei(test_pi[2,:].clone().detach(), test_mu[2,:].clone().detach(), test_sigma[2,:].clone().detach(), test_target[2].clone().detach(), test_input_data[2].clone().detach(),-(test_batch_id+102), opt.N_gaussians)
        # draw_mdn_wei(test_pi[3,:].clone().detach(), test_mu[3,:].clone().detach(), test_sigma[3,:].clone().detach(), test_target[3].clone().detach(), test_input_data[3].clone().detach(),-(test_batch_id+103), opt.N_gaussians)

        # pi = torch.cat([pi,torch.squeeze(test_pi.detach().cpu())],dim=0)
        # mu = torch.cat([mu,torch.squeeze(test_mu.detach().cpu())],dim=0)
        # sigma = torch.cat([sigma,torch.squeeze(test_sigma.detach().cpu())],dim=0)

========== IN Test dataset, NN Model + ASC:  6.365689277648926 ==========
========== IN Test dataset, the GTs + ASC: [[6.860111 8.893232]] ==========
========== The diff + ASC: 0.49442195892333984 ==========


- 研究下pi

In [457]:
# fixed
mlp.eval()
with torch.no_grad():
    #Compute the metric
    total_test_metric, GT_metric = validate(mlp,test_loader_fixed,opt.N_gaussians, opt.MIN_LOSS,device)
    draw_metric(0, total_test_metric.cpu(), GT_metric)
    print(f"========== IN Test dataset, NN Model + FIXED:  {total_test_metric.detach().cpu().numpy()} ==========")
    print(f"========== IN Test dataset, the GTs + FIXED: {GT_metric.detach().cpu().numpy()} ==========")
    print(f"========== The diff + Fixed: {GT_metric.detach().cpu().numpy()[0,0] - total_test_metric.detach().cpu().numpy()} ==========")

    # Save pi and mu sigma
    cnt = 0
    pi = torch.tensor([])
    mu = torch.tensor([])
    sigma = torch.tensor([])
    for test_batch_id, test_data in enumerate(test_loader_fixed):
        test_input_data, test_target, _, test_setting , test_metric = test_data
        test_input_data = test_input_data.to(device)
        test_target = test_target.to(device)
        cnt = cnt + len(test_input_data)
        test_pi, test_mu, test_sigma = mlp(test_input_data)

        # draw_mdn_wei(test_pi[0,:].clone().detach(), test_mu[0,:].clone().detach(), test_sigma[0,:].clone().detach(), test_target[0].clone().detach(), test_input_data[0].clone().detach(),-(test_batch_id+100), opt.N_gaussians)
        # draw_mdn_wei(test_pi[1,:].clone().detach(), test_mu[1,:].clone().detach(), test_sigma[1,:].clone().detach(), test_target[1].clone().detach(), test_input_data[1].clone().detach(),-(test_batch_id+101), opt.N_gaussians)
        # draw_mdn_wei(test_pi[2,:].clone().detach(), test_mu[2,:].clone().detach(), test_sigma[2,:].clone().detach(), test_target[2].clone().detach(), test_input_data[2].clone().detach(),-(test_batch_id+102), opt.N_gaussians)
        # draw_mdn_wei(test_pi[3,:].clone().detach(), test_mu[3,:].clone().detach(), test_sigma[3,:].clone().detach(), test_target[3].clone().detach(), test_input_data[3].clone().detach(),-(test_batch_id+103), opt.N_gaussians)

        pi = torch.cat([pi,torch.squeeze(test_pi.detach().cpu())],dim=0)
        mu = torch.cat([mu,torch.squeeze(test_mu.detach().cpu())],dim=0)
        sigma = torch.cat([sigma,torch.squeeze(test_sigma.detach().cpu())],dim=0)

========== IN Test dataset, NN Model + FIXED:  8.639244079589844 ==========
========== IN Test dataset, the GTs + FIXED: [[ 8.412077 14.403615]] ==========
========== The diff + Fixed: -0.22716712951660156 ==========
